# Zero-Shot and Translation Experiments on MLQA

If you're opening this Notebook on colab, you will need to moun drive and change directory.

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
%cd /content/drive/MyDrive/master/Applications2/project

/content/drive/.shortcut-targets-by-id/1AtJHZWX_djzvUvOzjyLFydMJ7eINbuMI/project


In [ ]:
%cd /content/drive/MyDrive/LAP/Subjects/AP2/project

/content/drive/MyDrive/LAP/Subjects/AP2/project


If you're opening this Notebook on colab, you will need to install 🤗 Transformers and 🤗 Datasets.

In [3]:
!pip install datasets transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 346 kB 5.3 MB/s 
     |████████████████████████████████| 4.2 MB 59.2 MB/s 
     |████████████████████████████████| 212 kB 69.8 MB/s 
     |████████████████████████████████| 86 kB 7.4 MB/s 
     |████████████████████████████████| 1.1 MB 64.7 MB/s 
     |████████████████████████████████| 86 kB 6.3 MB/s 
     |████████████████████████████████| 140 kB 61.8 MB/s 
     |████████████████████████████████| 596 kB 67.0 MB/s 
     |████████████████████████████████| 127 kB 73.0 MB/s 
     |████████████████████████████████| 6.6 MB 53.0 MB/s 
     |████████████████████████████████| 271 kB 68.4 MB/s 
     |████████████████████████████████| 144 kB 66.5 MB/s 
     |████████████████████████████████| 94 kB 4.5 MB/s 
     |████████████████████████████████| 112 kB 57.2 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling

To be able to share your model with the community and generate results like the one shown in the picture below via the inference API, there are a few more steps to follow.

First you have to store your authentication token from the Hugging Face website (sign up [here](https://huggingface.co/join) if you haven't already!) then execute the following cell and input your username and password:

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

## Load MLQA Dataset

MLQA (MultiLingual Question Answering) is a benchmark dataset for evaluating cross-lingual question answering performance. MLQA consists of over 5K extractive QA instances (12K in English) in SQuAD format in seven languages - English, Arabic, German, Spanish, Hindi, Vietnamese and Simplified Chinese. MLQA is highly parallel, with QA instances parallel between 4 different languages on average.

In [4]:
from datasets import load_dataset, load_metric

langs = ["ar", "de", "vi", "zh", "en", "es", "hi"]
translate_langs = ["ar", "de", "vi", "zh", "es", "hi"]
langs_test = []
langs_translate_test = []
langs_translate_train = ["ar.ar", "de.de", "vi.vi", "zh.zh", "en.en", "es.es", "hi.hi"]
langs_translate_train_all = []

mlqa = {}

for lang1 in langs:
    for lang2 in langs:
        mlqa[f"{lang1}.{lang2}"] = load_dataset("mlqa", f"mlqa.{lang1}.{lang2}")
        langs_test.append(f"{lang1}.{lang2}")

for lang in translate_langs:
    mlqa[f"translate-train.{lang}"] = load_dataset("mlqa", f"mlqa-translate-train.{lang}")
    mlqa[f"translate-test.{lang}"] = load_dataset("mlqa", f"mlqa-translate-test.{lang}")
    langs_translate_test.append(f"translate-test.{lang}")
    langs_translate_train_all.append(f"translate-train.{lang}")

Generating test split:   0%|          | 0/5335 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/517 [00:00<?, ? examples/s]

Dataset mlqa downloaded and prepared to /root/.cache/huggingface/datasets/mlqa/mlqa.ar.ar/1.0.0/224fde9ea61350ffb013e4beff31d44c6e125ce82c3aa4af70298eceabc8f7f7. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

Generating test split:   0%|          | 0/1649 [00:00<?, ? examples/s]

...

Dataset mlqa downloaded and prepared to /root/.cache/huggingface/datasets/mlqa/mlqa-translate-train.hi/1.0.0/224fde9ea61350ffb013e4beff31d44c6e125ce82c3aa4af70298eceabc8f7f7. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

Generating test split:   0%|          | 0/4918 [00:00<?, ? examples/s]

Dataset mlqa downloaded and prepared to /root/.cache/huggingface/datasets/mlqa/mlqa-translate-test.hi/1.0.0/224fde9ea61350ffb013e4beff31d44c6e125ce82c3aa4af70298eceabc8f7f7. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
mlqa

{'ar.ar': DatasetDict({
    test: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 5335
    })
    validation: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 517
    })
}),
 'ar.de': DatasetDict({
    test: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 1649
    })
    validation: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 207
    })
}),
 'ar.en': DatasetDict({
    test: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 5335
    })
    validation: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 517
    })
}),
 'ar.es': DatasetDict({
    test: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 1978
    })
    validation: Dataset({
        features: ['context', 'question', 'answers', 'id'],
        num_rows: 161

In [6]:
mlqa["en.es"]["test"][0]

{'answers': {'answer_start': [457],
  'text': ['Rutgers University biochemists']},
 'context': 'In 1994, five unnamed civilian contractors and the widows of contractors Walter Kasza and Robert Frost sued the USAF and the United States Environmental Protection Agency. Their suit, in which they were represented by George Washington University law professor Jonathan Turley, alleged they had been present when large quantities of unknown chemicals had been burned in open pits and trenches at Groom. Biopsies taken from the complainants were analyzed by Rutgers University biochemists, who found high levels of dioxin, dibenzofuran, and trichloroethylene in their body fat. The complainants alleged they had sustained skin, liver, and respiratory injuries due to their work at Groom, and that this had contributed to the deaths of Frost and Kasza. The suit sought compensation for the injuries they had sustained, claiming the USAF had illegally handled toxic materials, and that the EPA had failed in

In [7]:
mlqa["en.es"]["validation"][0]

{'answers': {'answer_start': [571],
  'text': ['remains infected for its lifetime']},
 'context': 'Pappataci fever is prevalent in the subtropical zone of the Eastern Hemisphere between 20°N and 45°N, particularly in Southern Europe, North Africa, the Balkans, Eastern Mediterranean, Iraq, Iran, Pakistan, Afghanistan and India.The disease is transmitted by the bites of phlebotomine sandflies of the Genus Phlebotomus, in particular, Phlebotomus papatasi, Phlebotomus perniciosus and Phlebotomus perfiliewi. The sandfly becomes infected when biting an infected human in the period between 48 hours before the onset of fever and 24 hours after the end of the fever, and remains infected for its lifetime. Besides this horizontal virus transmission from man to sandfly, the virus can be transmitted in insects transovarially, from an infected female sandfly to its offspring.Pappataci fever is seldom recognised in endemic populations because it is mixed with other febrile illnesses of childhood, but

In [8]:
mlqa["translate-train.es"]["train"][0]

{'answers': {'answer_start': [575], 'text': ['Santa Bernadette Soubirous']},
 'context': 'Arquitectónico, la escuela tiene un carácter católico. sobre la cúpula de oro del edificio principal es una estatua de oro de la Virgen María. inmediatamente frente al edificio principal y frente a ella, es una estatua de cobre de Cristo con los brazos levantado con la leyenda venite ad me omnes. junto al edificio principal se encuentra la Basílica del sagrado corazón. Inmediatamente detrás de la Basílica se encuentra la gruta, un lugar de oración y reflexión de Marian. Se trata de una réplica de la gruta en Lourdes, Francia, donde la Virgen María supuestamente apareció a saint bernadette soubirous en 1858. Al final de la unidad principal (y en una línea directa que conecta a través de 3 estatuas y la cúpula de oro), es una simple y moderna estatua de piedra de María.',
 'id': '5733be284776f41900661182',
 'question': 'A quién presuntamente apareció la Virgen María en 1858 en Lourdes Francia?'}

In [9]:
mlqa["translate-train.es"]["validation"][0]

{'answers': {'answer_start': [182, 182, 182],
  'text': ['DENVER BRONCOS', 'DENVER BRONCOS', 'DENVER BRONCOS']},
 'context': "Super Bowl 50 fue un juego de fútbol americano para determinar el campeón de la liga nacional de fútbol (NFL) para la temporada 2015 la conferencia de fútbol americano (AFC) campeón DENVER BRONCOS derrotó a la conferencia nacional de fútbol (NFC) Campeona Carolina Panthers 24-10 para ganar su tercer título de super bowl. El juego se jugó el 7 de febrero de 2016, en el estadio Levi ' s en la zona de la bahía de San Francisco en santa clara, California. Como este fue el 50º super bowl, la liga hizo hincapié en el aniversario de oro con varias iniciativas temáticas de oro, así como suspender temporalmente la tradición de nombrar cada juego de super bowl con números romanos (bajo el cual el juego habría sido conocido como super bowl l), de modo que el logotipo podría característica de forma prominente los números árabes 50.",
 'id': '56be4db0acb8001400a502ec',
 'que

In [10]:
mlqa["translate-test.es"]["test"][0]

{'answers': {'answer_start': [-1],
  'text': ['A Fan-shaped structures that followed a pattern of leaves, languages and lobes']},
 'context': 'After the eruption, the emissions of pyroclastic material that occurred from the gap created by the collapse were mostly magmatic origin, and in lower proportion of fragments of pre-existing volcanic rocks. The resulting deposits formed a fan-shaped structures that followed a pattern of leaves, languages and overlapping lobes. During the eruption of may 18, there were at least 17 emissions of pyroclastic flow separated over time, whose volumes of aggregation were around 208 million m3.',
 'id': 'b77c037b331e06542272669766df3b9515366b57',
 'question': 'What was the appearance of the deposits that left that landslide?'}

## Load SQuAD Dataset

Stanford Question Answering Dataset (SQuAD) is a reading comprehension dataset, consisting of questions posed by crowdworkers on a set of Wikipedia articles, where the answer to every question is a segment of text, or span, from the corresponding reading passage, or the question might be unanswerable. https://arxiv.org/pdf/1606.05250.pdf

In [ ]:
from datasets import load_dataset, load_metric

In [ ]:
squad = load_dataset("squad")

Extracting data files:   0%|          | 0/2 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/87599 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/10570 [00:00<?, ? examples/s]

Dataset squad downloaded and prepared to /root/.cache/huggingface/datasets/squad/plain_text/1.0.0/d6ec3ceb99ca480ce37cdd35555d6cb2511d223b9150cce08a837ef62ffea453. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
squad

DatasetDict({
    train: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 87599
    })
    validation: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 10570
    })
})

In [ ]:
squad["train"][0]

{'answers': {'answer_start': [515], 'text': ['Saint Bernadette Soubirous']},
 'context': 'Architecturally, the school has a Catholic character. Atop the Main Building\'s gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.',
 'id': '5733be284776f41900661182',
 'question': 'To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?',
 'title': 'University_of_Notre_Dame'}

In [ ]:
squad["validation"][0]

{'answers': {'answer_start': [177, 177, 177],
  'text': ['Denver Broncos', 'Denver Broncos', 'Denver Broncos']},
 'context': 'Super Bowl 50 was an American football game to determine the champion of the National Football League (NFL) for the 2015 season. The American Football Conference (AFC) champion Denver Broncos defeated the National Football Conference (NFC) champion Carolina Panthers 24–10 to earn their third Super Bowl title. The game was played on February 7, 2016, at Levi\'s Stadium in the San Francisco Bay Area at Santa Clara, California. As this was the 50th Super Bowl, the league emphasized the "golden anniversary" with various gold-themed initiatives, as well as temporarily suspending the tradition of naming each Super Bowl game with Roman numerals (under which the game would have been known as "Super Bowl L"), so that the logo could prominently feature the Arabic numerals 50.',
 'id': '56be4db0acb8001400a502ec',
 'question': 'Which NFL team represented the AFC at Super Bo

## Preprocessing SQuAD

Load the mBERT tokenizer to process the question and context fields.

In [ ]:
from transformers import AutoTokenizer

model_name = "bert-base-multilingual-cased"

tokenizer = AutoTokenizer.from_pretrained(model_name)

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/625 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/972k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.87M [00:00<?, ?B/s]

Now one specific thing for the preprocessing in question answering is how to deal with very long documents. We usually truncate them in other tasks, when they are longer than the model maximum sentence length, but here, removing part of the the context might result in losing the answer we are looking for. To deal with this, we will allow one (long) example in our dataset to give several input features, each of length shorter than the maximum length of the model (or the one we set as a hyper-parameter). Also, just in case the answer lies at the point we split a long context, we allow some overlap between the features we generate controlled by the hyper-parameter `doc_stride`:

In [11]:
max_length = 384 # The maximum length of a feature (question and context)
doc_stride = 128 # The authorized overlap between two part of the context when splitting it is needed.

There are a few preprocessing steps particular to question answering that we should be aware of:

1. Some examples in a dataset may have a very long context that exceeds the maximum input length of the model. Truncate only the context by setting `truncation="only_second"`.
2. Next, map the start and end positions of the answer to the original context by setting `return_offset_mapping=True`.
3. With the mapping in hand, you can find the start and end tokens of the answer. Use the `sequence_ids` method to find which part of the offset corresponds to the question and which corresponds to the `context`.

In [12]:
def prepare_train_features(examples):
    # Some of the questions have lots of whitespace on the left, which is not useful and will make the
    # truncation of the context fail (the tokenized question will take a lots of space). So we remove that
    # left whitespace
    examples["question"] = [q.lstrip() for q in examples["question"]]

    # Tokenize our examples with truncation and padding, but keep the overflows using a stride. This results
    # in one example possible giving several features when a context is long, each of those features having a
    # context that overlaps a bit the context of the previous feature.
    tokenized_examples = tokenizer(
        examples["question"],
        examples["context"],
        truncation="only_second",
        max_length=max_length,
        stride=doc_stride,
        return_overflowing_tokens=True,
        return_offsets_mapping=True,
        padding="max_length",
    )

    # Since one example might give us several features if it has a long context, we need a map from a feature to
    # its corresponding example. This key gives us just that.
    sample_mapping = tokenized_examples.pop("overflow_to_sample_mapping")
    # The offset mappings will give us a map from token to character position in the original context. This will
    # help us compute the start_positions and end_positions.
    offset_mapping = tokenized_examples.pop("offset_mapping")

    # Let's label those examples!
    tokenized_examples["start_positions"] = []
    tokenized_examples["end_positions"] = []

    for i, offsets in enumerate(offset_mapping):
        # We will label impossible answers with the index of the CLS token.
        input_ids = tokenized_examples["input_ids"][i]
        cls_index = input_ids.index(tokenizer.cls_token_id)

        # Grab the sequence corresponding to that example (to know what is the context and what is the question).
        sequence_ids = tokenized_examples.sequence_ids(i)

        # One example can give several spans, this is the index of the example containing this span of text.
        sample_index = sample_mapping[i]
        answers = examples["answers"][sample_index]
        # If no answers are given, set the cls_index as answer.
        if len(answers["answer_start"]) == 0:
            tokenized_examples["start_positions"].append(cls_index)
            tokenized_examples["end_positions"].append(cls_index)
        else:
            # Start/end character index of the answer in the text.
            start_char = answers["answer_start"][0]
            end_char = start_char + len(answers["text"][0])

            # Start token index of the current span in the text.
            token_start_index = 0
            while sequence_ids[token_start_index] != 1:
                token_start_index += 1

            # End token index of the current span in the text.
            token_end_index = len(input_ids) - 1
            while sequence_ids[token_end_index] != 1:
                token_end_index -= 1

            # Detect if the answer is out of the span (in which case this feature is labeled with the CLS index).
            if not (offsets[token_start_index][0] <= start_char and offsets[token_end_index][1] >= end_char):
                tokenized_examples["start_positions"].append(cls_index)
                tokenized_examples["end_positions"].append(cls_index)
            else:
                # Otherwise move the token_start_index and token_end_index to the two ends of the answer.
                # Note: we could go after the last offset if the answer is the last word (edge case).
                while token_start_index < len(offsets) and offsets[token_start_index][0] <= start_char:
                    token_start_index += 1
                tokenized_examples["start_positions"].append(token_start_index - 1)
                while offsets[token_end_index][1] >= end_char:
                    token_end_index -= 1
                tokenized_examples["end_positions"].append(token_end_index + 1)

    return tokenized_examples

Use 🤗 Datasets map function to apply the preprocessing function over the entire dataset. You can speed up the map function by setting `batched=True` to process multiple elements of the dataset at once. Remove the columns you don’t need.

In [ ]:
squad_train = squad.map(prepare_train_features, batched=True, 
                            remove_columns=squad["train"].column_names)

The evaluation features are similar to the train features. We have to check a given span is inside the context (and not the question) and how to get back the text inside. To do this, we need to add two things to our validation features:
- the ID of the example that generated the feature (since each example can generate several features, as seen before);
- the offset mapping that will give us a map from token indices to character positions in the context.

That's why we will re-process the validation set with the following function, slightly different from `prepare_train_features`:

In [13]:
def prepare_validation_features(examples):
    # Some of the questions have lots of whitespace on the left, which is not useful and will make the
    # truncation of the context fail (the tokenized question will take a lots of space). So we remove that
    # left whitespace
    examples["question"] = [q.lstrip() for q in examples["question"]]

    # Tokenize our examples with truncation and maybe padding, but keep the overflows using a stride. This results
    # in one example possible giving several features when a context is long, each of those features having a
    # context that overlaps a bit the context of the previous feature.
    tokenized_examples = tokenizer(
        examples["question"],
        examples["context"],
        truncation="only_second",
        max_length=max_length,
        stride=doc_stride,
        return_overflowing_tokens=True,
        return_offsets_mapping=True,
        padding="max_length",
    )

    # Since one example might give us several features if it has a long context, we need a map from a feature to
    # its corresponding example. This key gives us just that.
    sample_mapping = tokenized_examples.pop("overflow_to_sample_mapping")

    # We keep the example_id that gave us this feature and we will store the offset mappings.
    tokenized_examples["example_id"] = []

    for i in range(len(tokenized_examples["input_ids"])):
        # Grab the sequence corresponding to that example (to know what is the context and what is the question).
        sequence_ids = tokenized_examples.sequence_ids(i)
        context_index = 1
        
        # One example can give several spans, this is the index of the example containing this span of text.
        sample_index = sample_mapping[i]
        tokenized_examples["example_id"].append(examples["id"][sample_index])

        # Set to None the offset_mapping that are not part of the context so it's easy to determine if a token
        # position is part of the context or not.
        tokenized_examples["offset_mapping"][i] = [
            (o if sequence_ids[k] == context_index else None)
            for k, o in enumerate(tokenized_examples["offset_mapping"][i])
        ]

    return tokenized_examples

Use the map function again to apply the preprocessing function over the validation dataset. You can speed up the map function by setting `batched=True` to process multiple elements of the dataset at once. Remove the columns you don’t need.

In [ ]:
squad_eval = squad["validation"].map(prepare_validation_features, batched=True, 
                                          remove_columns=squad["validation"].column_names)

## Fine-tuning mBERT

Now that our data is ready for training, we can download the pretrained model and fine-tune it. Since our task is question answering, we use the `AutoModelForQuestionAnswering` class. Like with the tokenizer, the `from_pretrained` method will download and cache the model for us:

In [ ]:
from transformers import AutoModelForQuestionAnswering, TrainingArguments, Trainer

model_name = "bert-base-multilingual-cased"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)

Downloading:   0%|          | 0.00/681M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertForQuestionAnswering from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForQuestionAnswering from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at bert-bas

Then we will need a data collator that will batch our processed examples together, here the default one will work:

In [ ]:
from transformers import DefaultDataCollator

data_collator = DefaultDataCollator()

To instantiate a `Trainer`, we will need to define three more things. The most important is the [`TrainingArguments`](https://huggingface.co/transformers/main_classes/trainer.html#transformers.TrainingArguments), which is a class that contains all the attributes to customize the training. It requires one folder name, which will be used to save the checkpoints of the model, and all other arguments are optional:

In [ ]:
batch_size = 16
args = TrainingArguments(
    "bert-base-multilingual-cased-squad",
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
    # push_to_hub=True,
)

We will evaluate our model and compute metrics in the next section (this is a very long operation, so we will only compute the evaluation loss during training).

Then we just need to pass all of this along with our datasets to the `Trainer`:

In [ ]:
trainer = Trainer(
    model,
    args,
    train_dataset=squad_train["train"],
    eval_dataset=squad_train["validation"],
    data_collator=data_collator,
    tokenizer=tokenizer,
)

We can now finetune our model by just calling the `train` method:

In [ ]:
# trainer.train()

In [ ]:
# trainer.push_to_hub()

## Evaluating mBERT

We load a model that is already finetuned on SQuAD to save time. We evaluate on the validation set of SQuAD.

In [ ]:
from transformers import AutoModelForQuestionAnswering, TrainingArguments, Trainer

model_name = "salti/bert-base-multilingual-cased-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bert-base-multilingual-cased-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpqsh2ch2_


Downloading:   0%|          | 0.00/822 [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
creating metadata file for /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
loading configuration file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
Model config BertConfig {
  "_name_or_path": "salti/bert-base-multilingual-cased-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_d

Downloading:   0%|          | 0.00/676M [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
creating metadata file for /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
loading weights file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
All model checkpoint weights were used when initializing BertForQuestionAnswering.

All the weights of BertForQuestionAnswering were initialized from the model checkpoint at salti/bert-base-multilingual-c

...

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/834c4d17cccdc848e5ac1e4978b371d9d3afa3bb371fe8f6be85119e3a0ea885.c60f034cf5bf819518a0170960ddb62b4576fa3d01e9021876b801600cbb6f42
creating metadata file for /root/.cache/huggingface/transformers/834c4d17cccdc848e5ac1e4978b371d9d3afa3bb371fe8f6be85119e3a0ea885.c60f034cf5bf819518a0170960ddb62b4576fa3d01e9021876b801600cbb6f42
loading configuration file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
Model config BertConfig {
  "_name_or_path": "salti/bert-base-multilingual-cased-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "cl

Downloading:   0%|          | 0.00/972k [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/vocab.txt in cache at /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
creating metadata file for /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp1z0rang8


Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/33bece2c5789380abddaab5941fb528198297c167ddfa9547ab37dd92f940b55.dd8bd9bfd3664b530ea4e645105f557769387b3da9f79bdb55ed556bdd80611d
creating metadata file for /root/.cache/huggingface/transformers/33bece2c5789380abddaab5941fb528198297c167ddfa9547ab37dd92f940b55.dd8bd9bfd3664b530ea4e645105f557769387b3da9f79bdb55ed556bdd80611d
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/vocab.txt from cache at /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/tokenizer.json from cache at None
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned

We can grab the predictions for all features by using the `Trainer.predict` method:

In [ ]:
raw_predictions = trainer.predict(squad_eval)

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 10851
  Batch size = 16


The `Trainer` *hides* the columns that are not used by the model (here `example_id` and `offset_mapping` which we will need for our post-processing), so we set them back:

In [ ]:
squad_eval.set_format(type=squad_eval.format["type"], 
                      columns=list(squad_eval.features.keys()))

We can now refine the test we had before: since we set `None` in the offset mappings when it corresponds to a part of the question, it's easy to check if an answer is fully inside the context. We also eliminate very long answers from our considerations (with an hyper-parameter we can tune)

As we mentioned in the code above, this was easy on the first feature because we knew it comes from the first example. For the other features, we will need a map between examples and their corresponding features. Also, since one example can give several features, we will need to gather together all the answers in all the features generated by a given example, then pick the best one. The following code builds a map from example index to its corresponding features indices.

In [14]:
from tqdm.auto import tqdm
import collections
import numpy as np

def postprocess_qa_predictions(examples, features, raw_predictions, n_best_size = 20, max_answer_length = 30):
    all_start_logits, all_end_logits = raw_predictions
    # Build a map example to its corresponding features.
    example_id_to_index = {k: i for i, k in enumerate(examples["id"])}
    features_per_example = collections.defaultdict(list)
    for i, feature in enumerate(features):
        features_per_example[example_id_to_index[feature["example_id"]]].append(i)

    # The dictionaries we have to fill.
    predictions = collections.OrderedDict()

    # Logging.
    print(f"Post-processing {len(examples)} example predictions split into {len(features)} features.")

    # Let's loop over all the examples!
    for example_index, example in enumerate(tqdm(examples)):
        # Those are the indices of the features associated to the current example.
        feature_indices = features_per_example[example_index]

        valid_answers = []
        
        context = example["context"]
        # Looping through all the features associated to the current example.
        for feature_index in feature_indices:
            # We grab the predictions of the model for this feature.
            start_logits = all_start_logits[feature_index]
            end_logits = all_end_logits[feature_index]
            # This is what will allow us to map some the positions in our logits to span of texts in the original
            # context.
            offset_mapping = features[feature_index]["offset_mapping"]

            # Go through all possibilities for the `n_best_size` greater start and end logits.
            start_indexes = np.argsort(start_logits)[-1 : -n_best_size - 1 : -1].tolist()
            end_indexes = np.argsort(end_logits)[-1 : -n_best_size - 1 : -1].tolist()
            for start_index in start_indexes:
                for end_index in end_indexes:
                    # Don't consider out-of-scope answers, either because the indices are out of bounds or correspond
                    # to part of the input_ids that are not in the context.
                    if (
                        start_index >= len(offset_mapping)
                        or end_index >= len(offset_mapping)
                        or offset_mapping[start_index] is None
                        or offset_mapping[end_index] is None
                    ):
                        continue
                    # Don't consider answers with a length that is either < 0 or > max_answer_length.
                    if end_index < start_index or end_index - start_index + 1 > max_answer_length:
                        continue

                    start_char = offset_mapping[start_index][0]
                    end_char = offset_mapping[end_index][1]
                    valid_answers.append(
                        {
                            "score": start_logits[start_index] + end_logits[end_index],
                            "text": context[start_char: end_char]
                        }
                    )
        
        if len(valid_answers) > 0:
            best_answer = sorted(valid_answers, key=lambda x: x["score"], reverse=True)[0]
        else:
            # In the very rare edge case we have not a single non-null prediction, we create a fake prediction to avoid
            # failure.
            best_answer = {"text": "", "score": 0.0}
        
        # Let's pick our final answer: the best one
        predictions[example["id"]] = best_answer["text"]

    return predictions

And we can apply our post-processing function to our raw predictions:

In [ ]:
final_predictions = postprocess_qa_predictions(squad["validation"], squad_eval, raw_predictions.predictions)

Post-processing 10570 example predictions split into 10851 features.


  0%|          | 0/10570 [00:00<?, ?it/s]

Then we can load the metric from the datasets library.

In [21]:
metric = load_metric("squad")

Then we can call compute on it. We just need to format predictions and labels a bit as it expects a list of dictionaries and not one big dictionary.

In [ ]:
formatted_predictions = [{"id": k, "prediction_text": v} for k, v in final_predictions.items()]
references = [{"id": ex["id"], "answers": ex["answers"]} for ex in squad["validation"]]
metric.compute(predictions=formatted_predictions, references=references)

{'exact_match': 81.90160832544939, 'f1': 89.121876471452}

## Zero-Shot mBERT

Zero-Shot performance of the mBERT model fine-tuned on SQuAD.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "salti/bert-base-multilingual-cased-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bert-base-multilingual-cased-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

loading configuration file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
Model config BertConfig {
  "_name_or_path": "salti/bert-base-multilingual-cased-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "gradient_checkpointing": false,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "pad_token_id": 0,
  "pooler_fc_size": 768,
  "pooler_num_attention_heads": 12,
  "pooler_num_fc_layers": 3,
  "pooler_size_per

Use the map function again to apply the preprocessing function over the validation dataset. You can speed up the map function by setting `batched=True` to process multiple elements of the dataset at once. Remove the columns you don’t need.

In [15]:
from collections import defaultdict

mlqa_prep = defaultdict(dict)

def map_datasets(langs, split, prepare_features):
    for lang in langs:
        mlqa_prep[lang][split] = mlqa[lang][split].map(prepare_features, batched=True, 
                                    remove_columns=mlqa[lang][split].column_names)

In [ ]:
split = "test"
map_datasets(langs_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

...

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [16]:
def compute_results(langs, split):
    results = {}
    for lang in langs:
        # We can grab the predictions for all features by using the method
        raw_predictions = trainer.predict(mlqa_prep[lang][split])

        # example_id and offset_mapping which we will need for our post-processing
        mlqa_prep[lang][split].set_format(type=mlqa_prep[lang][split].format["type"], 
                        columns=list(mlqa_prep[lang][split].features.keys()))
        
        # And we can apply our post-processing function to our raw predictions
        final_predictions = postprocess_qa_predictions(mlqa[lang][split], mlqa_prep[lang][split], raw_predictions.predictions)

        # We just need to format predictions and labels a bit as it expects a list of dictionaries and not one big dictionary.
        formatted_predictions = [{"id": k, "prediction_text": v} for k, v in final_predictions.items()]
        references = [{"id": ex["id"], "answers": ex["answers"]} for ex in mlqa[lang][split]]
        results[lang] = metric.compute(predictions=formatted_predictions, references=references)
    return results

In [ ]:
results_zero_shot_mbert = compute_results(langs_test, split)
print(results_zero_shot_mbert)

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 7534
  Batch size = 16


Post-processing 5335 example predictions split into 7534 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 2090
  Batch size = 16


Post-processing 1649 example predictions split into 2090 features.


...

  0%|          | 0/1723 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 7500
  Batch size = 16


Post-processing 4918 example predictions split into 7500 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'ar.ar': {'exact_match': 28.02249297094658, 'f1': 44.929516784532346}, 'ar.de': {'exact_match': 30.503335354760463, 'f1': 46.34281596858772}, 'ar.vi': {'exact_match': 20.078163165608206, 'f1': 35.855170013530305}, 'ar.zh': {'exact_match': 21.286610878661087, 'f1': 36.836139618796864}, 'ar.en': {'exact_match': 33.68322399250234, 'f1': 51.05706234227977}, 'ar.es': {'exact_match': 28.665318503538927, 'f1': 45.39895834649171}, 'ar.hi': {'exact_match': 17.312943746586566, 'f1': 30.78874873874883}, 'de.ar': {'exact_match': 23.650697392359007, 'f1': 36.746358156228915}, 'de.de': {'exact_match': 43.74584901483286, 'f1': 59.39314267422581}, 'de.vi': {'exact_match': 29.611940298507463, 'f1': 43.59122326994722}, 'de.zh': {'exact_match': 30.66008636644047, 'f1': 46.46878322661527}, 'de.en': {'exact_match': 46.734558335178214, 'f1': 62.361949176983636}, 'de.es': {'exact_match': 40.990990990990994, 'f1': 56.37397727738263}, 'de.hi': {'exact_match': 21.53846153846154, 'f1': 34.05070095047693}, 'vi.a

In [17]:
import pandas as pd
def results_df(results_dict, model):
    F1colname = "F1_" + model
    EMcolname = "EM_" + model
    dict_results = defaultdict(list)
    for lang, scores in results_dict.items():
        dict_results["lang"].append(lang)
        dict_results[F1colname].append(scores['f1'])
        dict_results[EMcolname].append(scores['exact_match'])

    avg_f1 = np.average(dict_results[F1colname])
    avg_em = np.average(dict_results[EMcolname])
    dict_results["lang"].append('avg')
    dict_results[F1colname].append(avg_f1)
    dict_results[EMcolname].append(avg_em)
    df_results = pd.DataFrame(dict_results).round(2)
    return df_results

In [ ]:
df_results_zero_shot_mbert = results_df(results_zero_shot_mbert, "Zero-shot mBERT")
df_results_zero_shot_mbert.to_csv("results/mlqa/results_zero_shot_mbert.csv")
df_results_zero_shot_mbert

lang  F1_Zero-shot mBERT  EM_Zero-shot mBERT
0   ar.ar               44.93               28.02
1   ar.de               46.34               30.50
2   ar.vi               35.86               20.08
3   ar.zh               36.84               21.29
4   ar.en               51.06               33.68
5   ar.es               45.40               28.67
6   ar.hi               30.79               17.31
7   de.ar               36.75               23.65
8   de.de               59.39               43.75
9   de.vi               43.59               29.61
10  de.zh               46.47               30.66
11  de.en               62.36               46.73
12  de.es               56.37               40.99
13  de.hi               34.05               21.54
14  vi.ar               32.47               19.30
15  vi.de               53.68               36.60
16  vi.vi               58.80               39.56
17  vi.zh               50.27               32.27
18  vi.en               64.54               44.80
19  vi.es               53.87               37.46
20  vi.hi               35.09               19.72
21  zh.ar               20.96               20.55
22  zh.de               29.96               28.93
23  zh.vi               25.07               24.40
24  zh.zh               37.38               36.79
25  zh.en               38.30               37.67
26  zh.es               29.00               28.30
27  zh.hi               16.65               16.19
28  en.ar               44.14               31.06
29  en.de               66.43               52.47
30  en.vi               53.71               39.13
31  en.zh               55.77               41.37
32  en.en               80.30               67.02
33  en.es               67.38               52.75
34  en.hi               39.27               26.27
35  es.ar               43.13               26.04
36  es.de               60.59               40.20
37  es.vi               48.46               31.37
38  es.zh               49.87               30.56
39  es.en               66.93               46.39
40  es.es               64.88               43.61
41  es.hi               36.17               20.08
42  hi.ar               34.50               21.35
43  hi.de               47.55               33.85
44  hi.vi               38.04               25.01
45  hi.zh               39.25               25.24
46  hi.en               52.90               37.11
47  hi.es               43.73               29.08
48  hi.hi               46.21               30.01
49    avg               46.03               32.43

## Zero-Shot XLM-R

Zero-Shot performance of the XLM-R model fine-tuned on SQuAD.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "vanichandna/xlm-roberta-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name,from_tf=True)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

loading configuration file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/6e9fab04c4168068e4162152496d68d0594b8a838953657e9234b70b2c4932fb.b04b4828cf6cfcbbcba34b7e4fc29fe9a0563001f3cedda0f9cf6487875eae92
Model config XLMRobertaConfig {
  "_name_or_path": "vanichandna/xlm-roberta-finetuned-squad",
  "architectures": [
    "XLMRobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id": 2,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "xlm-roberta",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "output_past": true,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "transformers_version": "4.19.2",
  "type_vocab_size": 1,
  "use_c

In [ ]:
split = "test"
map_datasets(langs_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

...

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_zero_shot_xlm_r = compute_results(langs_test, split)
print(results_zero_shot_xlm_r)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6810
  Batch size = 16


Post-processing 5335 example predictions split into 6810 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 1962
  Batch size = 16


Post-processing 1649 example predictions split into 1962 features.


...

  0%|          | 0/1723 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6351
  Batch size = 16


Post-processing 4918 example predictions split into 6351 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'ar.ar': {'exact_match': 36.04498594189316, 'f1': 54.57451581160068}, 'ar.de': {'exact_match': 19.83020012128563, 'f1': 34.25263888728561}, 'ar.vi': {'exact_match': 5.666829506595017, 'f1': 14.94639212385503}, 'ar.zh': {'exact_match': 5.125523012552302, 'f1': 14.068779407705085}, 'ar.en': {'exact_match': 33.77694470477976, 'f1': 51.47313049087474}, 'ar.es': {'exact_match': 13.498483316481295, 'f1': 26.94704044141251}, 'ar.hi': {'exact_match': 5.843801201529219, 'f1': 15.607909297684078}, 'de.ar': {'exact_match': 12.067919951485749, 'f1': 22.218681685415685}, 'de.de': {'exact_match': 46.734558335178214, 'f1': 62.19529747175471}, 'de.vi': {'exact_match': 16.17910447761194, 'f1': 28.730980236546745}, 'de.zh': {'exact_match': 17.14990746452807, 'f1': 29.078124173787472}, 'de.en': {'exact_match': 44.2993137037857, 'f1': 59.94603497539026}, 'de.es': {'exact_match': 29.72972972972973, 'f1': 43.999710609466405}, 'de.hi': {'exact_match': 17.622377622377623, 'f1': 29.40625968950811}, 'vi.ar': {

In [ ]:
df_results_zero_shot_xlm_r = results_df(results_zero_shot_xlm_r, "Zero-shot XML-R")
df_results_zero_shot_xlm_r.to_csv("results/mlqa/results_zero_shot_xlm_r.csv")
df_results_zero_shot_xlm_r

lang  F1_Zero-shot XML-R  EM_Zero-shot XML-R
0   ar.ar               54.57               36.04
1   ar.de               34.25               19.83
2   ar.vi               14.95                5.67
3   ar.zh               14.07                5.13
4   ar.en               51.47               33.78
5   ar.es               26.95               13.50
6   ar.hi               15.61                5.84
7   de.ar               22.22               12.07
8   de.de               62.20               46.73
9   de.vi               28.73               16.18
10  de.zh               29.08               17.15
11  de.en               59.95               44.30
12  de.es               44.00               29.73
13  de.hi               29.41               17.62
14  vi.ar               17.75                6.64
15  vi.de               41.92               25.73
16  vi.vi               67.15               46.31
17  vi.zh               27.37               13.79
18  vi.en               63.61               44.57
19  vi.es               32.63               19.08
20  vi.hi               29.25               14.95
21  zh.ar                3.87                3.66
22  zh.de               14.01               13.26
23  zh.vi                8.08                7.67
24  zh.zh               39.96               39.34
25  zh.en               34.92               34.30
26  zh.es               11.33               10.73
27  zh.hi               10.79               10.41
28  en.ar               33.54               21.31
29  en.de               60.75               47.13
30  en.vi               39.83               27.53
31  en.zh               37.92               25.29
32  en.en               80.78               68.02
33  en.es               57.84               43.92
34  en.hi               44.97               32.03
35  es.ar               25.15               12.29
36  es.de               50.50               32.60
37  es.vi               29.07               14.87
38  es.zh               28.19               14.33
39  es.en               65.96               45.08
40  es.es               66.53               46.09
41  es.hi               31.81               17.06
42  hi.ar               19.47                7.97
43  hi.de               42.80               27.83
44  hi.vi               24.32               11.92
45  hi.zh               26.06               13.58
46  hi.en               60.59               43.41
47  hi.es               37.39               23.04
48  hi.hi               61.35               44.23
49    avg               37.04               24.77

## Zero-Shot XLM-R-large

Zero-Shot performance of the XLM-R-large model fine-tuned on SQuAD.

In [24]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "Palak/xlm-roberta-large_squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-large_squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpfcokta8s


Downloading:   0%|          | 0.00/718 [00:00<?, ?B/s]

storing https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/15ba31e9d5d227c3e7514429b9e154b4dd9fa20dc6634e2aa859a6570580ab8a.e0ee6561aeb1e6c81ca8555d0aed71ddc7b312c694416a29b2dd0b16df13a0b3
creating metadata file for /root/.cache/huggingface/transformers/15ba31e9d5d227c3e7514429b9e154b4dd9fa20dc6634e2aa859a6570580ab8a.e0ee6561aeb1e6c81ca8555d0aed71ddc7b312c694416a29b2dd0b16df13a0b3
loading configuration file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/15ba31e9d5d227c3e7514429b9e154b4dd9fa20dc6634e2aa859a6570580ab8a.e0ee6561aeb1e6c81ca8555d0aed71ddc7b312c694416a29b2dd0b16df13a0b3
Model config XLMRobertaConfig {
  "_name_or_path": "Palak/xlm-roberta-large_squad",
  "architectures": [
    "XLMRobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id

Downloading:   0%|          | 0.00/2.08G [00:00<?, ?B/s]

storing https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/8edefbae0f1cc20d5925e7aeb8dd97881317810b29b16f0b519cabf0cd976fcb.7a0fe9d2258fd179f0fd3372c78a7daa343f8f5fcacba19a70f8f4bfcfa6a3a6
creating metadata file for /root/.cache/huggingface/transformers/8edefbae0f1cc20d5925e7aeb8dd97881317810b29b16f0b519cabf0cd976fcb.7a0fe9d2258fd179f0fd3372c78a7daa343f8f5fcacba19a70f8f4bfcfa6a3a6
loading weights file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/8edefbae0f1cc20d5925e7aeb8dd97881317810b29b16f0b519cabf0cd976fcb.7a0fe9d2258fd179f0fd3372c78a7daa343f8f5fcacba19a70f8f4bfcfa6a3a6
All model checkpoint weights were used when initializing XLMRobertaForQuestionAnswering.

All the weights of XLMRobertaForQuestionAnswering were initialized from the model checkpoint at Palak/xlm-roberta-large_squad.
If your task is similar to th

...

storing https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/58308abdd398f5feffa9aaff656219b64ebd9236ce9da250378bf5d560485a10.a5d1dac1ca7c1325c3e25e67943f907355e16d3ce944debef21145a8e417ec71
creating metadata file for /root/.cache/huggingface/transformers/58308abdd398f5feffa9aaff656219b64ebd9236ce9da250378bf5d560485a10.a5d1dac1ca7c1325c3e25e67943f907355e16d3ce944debef21145a8e417ec71
https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp47h88qxv


Downloading:   0%|          | 0.00/8.66M [00:00<?, ?B/s]

storing https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/2fffb1a5f7088f56e8cf5dc66ec6591aa646135b32a7303334a91515de51e4b9.2dedbd3aa2bb53e8e26ed0125daf18f6d4aeeeeb98252d7ce59b3a63d810a963
creating metadata file for /root/.cache/huggingface/transformers/2fffb1a5f7088f56e8cf5dc66ec6591aa646135b32a7303334a91515de51e4b9.2dedbd3aa2bb53e8e26ed0125daf18f6d4aeeeeb98252d7ce59b3a63d810a963
https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpg5pq5t3y


Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

storing https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/650b29e8bb4961f982ce7a003c8ff1fb431803ef3eedb3740f602256eaee04ef.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
creating metadata file for /root/.cache/huggingface/transformers/650b29e8bb4961f982ce7a003c8ff1fb431803ef3eedb3740f602256eaee04ef.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
loading file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/sentencepiece.bpe.model from cache at None
loading file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/2fffb1a5f7088f56e8cf5dc66ec6591aa646135b32a7303334a91515de51e4b9.2dedbd3aa2bb53e8e26ed0125daf18f6d4aeeeeb98252d7ce59b3a63d810a963
loading file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/added_tokens.json from cache at None
loading file 

In [25]:
split = "test"
map_datasets(langs_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/3 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

...

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/2 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [26]:
results_zero_shot_xlm_r_large = compute_results(langs_test, split)
print(results_zero_shot_xlm_r_large)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6810
  Batch size = 16


Post-processing 5335 example predictions split into 6810 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 1962
  Batch size = 16


Post-processing 1649 example predictions split into 1962 features.


...

  0%|          | 0/1723 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6351
  Batch size = 16


Post-processing 4918 example predictions split into 6351 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'ar.ar': {'exact_match': 42.080599812558575, 'f1': 62.04049045858398}, 'ar.de': {'exact_match': 41.84354154032747, 'f1': 59.72543726976998}, 'ar.vi': {'exact_match': 30.72789447972643, 'f1': 48.63589464106053}, 'ar.zh': {'exact_match': 21.60041841004184, 'f1': 38.74264374763998}, 'ar.en': {'exact_match': 42.23055295220244, 'f1': 61.72362599767862}, 'ar.es': {'exact_match': 38.42264914054601, 'f1': 56.73926106550734}, 'ar.hi': {'exact_match': 27.416712179137082, 'f1': 43.93756848280634}, 'de.ar': {'exact_match': 19.52698605215282, 'f1': 31.223498725317143}, 'de.de': {'exact_match': 52.379898162497234, 'f1': 68.47435650082255}, 'de.vi': {'exact_match': 34.26865671641791, 'f1': 50.66677826761544}, 'de.zh': {'exact_match': 18.9389265885256, 'f1': 32.29150355243454}, 'de.en': {'exact_match': 51.693601948195706, 'f1': 67.72892927070916}, 'de.es': {'exact_match': 49.549549549549546, 'f1': 65.32197525218696}, 'de.hi': {'exact_match': 21.888111888111887, 'f1': 36.14938366542679}, 'vi.ar': {'ex

In [27]:
df_results_zero_shot_xlm_r_large = results_df(results_zero_shot_xlm_r_large, "Zero-shot XML-R Large")
df_results_zero_shot_xlm_r_large.to_csv("results/mlqa/results_zero_shot_xlm_r_large.csv")
df_results_zero_shot_xlm_r_large

lang  F1_Zero-shot XML-R Large  EM_Zero-shot XML-R Large
0   ar.ar                     62.04                     42.08
1   ar.de                     59.73                     41.84
2   ar.vi                     48.64                     30.73
3   ar.zh                     38.74                     21.60
4   ar.en                     61.72                     42.23
5   ar.es                     56.74                     38.42
6   ar.hi                     43.94                     27.42
7   de.ar                     31.22                     19.53
8   de.de                     68.47                     52.38
9   de.vi                     50.67                     34.27
10  de.zh                     32.29                     18.94
11  de.en                     67.73                     51.69
12  de.es                     65.32                     49.55
13  de.hi                     36.15                     21.89
14  vi.ar                     35.76                     20.86
15  vi.de                     67.68                     48.24
16  vi.vi                     73.06                     51.79
17  vi.zh                     39.24                     21.67
18  vi.en                     72.08                     50.88
19  vi.es                     64.66                     45.49
20  vi.hi                     42.00                     25.27
21  zh.ar                     25.91                     25.42
22  zh.de                     41.08                     40.22
23  zh.vi                     34.99                     34.59
24  zh.zh                     45.69                     45.07
25  zh.en                     44.23                     43.64
26  zh.es                     36.71                     36.11
27  zh.hi                     29.95                     29.49
28  en.ar                     32.44                     22.06
29  en.de                     77.67                     65.09
30  en.vi                     61.55                     48.54
31  en.zh                     33.80                     21.12
32  en.en                     83.97                     71.18
33  en.es                     77.24                     64.21
34  en.hi                     43.64                     30.68
35  es.ar                     32.96                     17.75
36  es.de                     69.96                     48.65
37  es.vi                     54.83                     35.63
38  es.zh                     36.47                     20.54
39  es.en                     72.09                     50.31
40  es.es                     72.11                     50.16
41  es.hi                     42.10                     26.12
42  hi.ar                     45.51                     29.11
43  hi.de                     65.07                     49.93
44  hi.vi                     54.38                     37.65
45  hi.zh                     44.58                     28.52
46  hi.en                     70.51                     52.56
47  hi.es                     63.25                     45.91
48  hi.hi                     69.83                     51.30
49    avg                     52.66                     38.33

## Translate Test BERT

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we use a monolingual BERT model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "rsvp-ai/bertserini-bert-base-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bertserini-bert-base-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

Downloading:   0%|          | 0.00/477 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/418M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_bert = compute_results(langs_translate_test, split)
print(results_translate_test_bert)

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6129
  Batch size = 16


Post-processing 5335 example predictions split into 6129 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 4969
  Batch size = 16


Post-processing 4517 example predictions split into 4969 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5491
  Batch size = 16


Post-processing 4918 example predictions split into 5491 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 27.74133083411434, 'f1': 50.99569306582404}, 'translate-test.de': {'exact_match': 35.73168031879566, 'f1': 54.38737847879753}, 'translate-test.vi': {'exact_match': 32.08371246587807, 'f1': 53.56689765843997}, 'translate-test.zh': {'exact_match': 26.649795600545065, 'f1': 47.846129141598}, 'translate-test.es': {'exact_match': 43.15629164287074, 'f1': 64.96039910994322}, 'translate-test.hi': {'exact_match': 32.04554697031313, 'f1': 52.84132138420167}}


In [ ]:
df_results_translate_test_bert = results_df(results_translate_test_bert, "Translate-test BERT")
df_results_translate_test_bert.to_csv("results/mlqa/results_translate_test_bert.csv")
df_results_translate_test_bert

lang  F1_Translate-test BERT  EM_Translate-test BERT
0  translate-test.ar                   51.00                   27.74
1  translate-test.de                   54.39                   35.73
2  translate-test.vi                   53.57                   32.08
3  translate-test.zh                   47.85                   26.65
4  translate-test.es                   64.96                   43.16
5  translate-test.hi                   52.84                   32.05
6                avg                   54.10                   32.90

## Translate Test BERT-large

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we use a monolingual BERT-large model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "bert-large-cased-whole-word-masking-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="dir-bert-large-cased-whole-word-masking-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp9aldjmfh


Downloading:   0%|          | 0.00/634 [00:00<?, ?B/s]

storing https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/09a6ac8433ff705d719a8e60cb1588e83d2220da2cfe95905e958496c092535c.e15ff0ac80307dd3e1ae18a41ec3b31fef893cd86ef240a21ccd2e44dc175ee5
creating metadata file for /root/.cache/huggingface/transformers/09a6ac8433ff705d719a8e60cb1588e83d2220da2cfe95905e958496c092535c.e15ff0ac80307dd3e1ae18a41ec3b31fef893cd86ef240a21ccd2e44dc175ee5
loading configuration file https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/09a6ac8433ff705d719a8e60cb1588e83d2220da2cfe95905e958496c092535c.e15ff0ac80307dd3e1ae18a41ec3b31fef893cd86ef240a21ccd2e44dc175ee5
Model config BertConfig {
  "_name_or_path": "bert-large-cased-whole-word-masking-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifie

Downloading:   0%|          | 0.00/1.24G [00:00<?, ?B/s]

storing https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/53388cf41351c777622f6d7afdf706d7d7d5c4a05a33791985136ef7dddc7c43.53f4a814c8affef829fa2203ae222c8c013fb980860c34a0043b12ba52d16f0b
creating metadata file for /root/.cache/huggingface/transformers/53388cf41351c777622f6d7afdf706d7d7d5c4a05a33791985136ef7dddc7c43.53f4a814c8affef829fa2203ae222c8c013fb980860c34a0043b12ba52d16f0b
loading weights file https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/53388cf41351c777622f6d7afdf706d7d7d5c4a05a33791985136ef7dddc7c43.53f4a814c8affef829fa2203ae222c8c013fb980860c34a0043b12ba52d16f0b
All model checkpoint weights were used when initializing BertForQuestionAnswering.

All the weights of BertForQuestionAnswering were initialized from the model checkpoint at bert-large-cased-whole-word-

...

storing https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/0055368eb34542f93de5eb70c2a9c3a059bd01bae2628a405905dbc882701901.ec5c189f89475aac7d8cbd243960a0655cfadc3d0474da8ff2ed0bf1699c2a5f
creating metadata file for /root/.cache/huggingface/transformers/0055368eb34542f93de5eb70c2a9c3a059bd01bae2628a405905dbc882701901.ec5c189f89475aac7d8cbd243960a0655cfadc3d0474da8ff2ed0bf1699c2a5f
loading configuration file https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/09a6ac8433ff705d719a8e60cb1588e83d2220da2cfe95905e958496c092535c.e15ff0ac80307dd3e1ae18a41ec3b31fef893cd86ef240a21ccd2e44dc175ee5
Model config BertConfig {
  "_name_or_path": "bert-large-cased-whole-word-masking-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  

Downloading:   0%|          | 0.00/208k [00:00<?, ?B/s]

storing https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/vocab.txt in cache at /root/.cache/huggingface/transformers/f77a43252a6dcf4565bb023e211c0f71c8b11ec71cae167d4e2fb1ec8dee9a87.437aa611e89f6fc6675a049d2b5545390adbc617e7d655286421c191d2be2791
creating metadata file for /root/.cache/huggingface/transformers/f77a43252a6dcf4565bb023e211c0f71c8b11ec71cae167d4e2fb1ec8dee9a87.437aa611e89f6fc6675a049d2b5545390adbc617e7d655286421c191d2be2791
https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp5f6eyql7


Downloading:   0%|          | 0.00/426k [00:00<?, ?B/s]

storing https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/7e7140ff927e58a37a0862cd3dc4e2873c713af14eaf32a602d99be03d11bbb4.2b9a196704f2f183fe3f4b48d6e662dba8203fdcb3346bfa896831378edf6f97
creating metadata file for /root/.cache/huggingface/transformers/7e7140ff927e58a37a0862cd3dc4e2873c713af14eaf32a602d99be03d11bbb4.2b9a196704f2f183fe3f4b48d6e662dba8203fdcb3346bfa896831378edf6f97
loading file https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/vocab.txt from cache at /root/.cache/huggingface/transformers/f77a43252a6dcf4565bb023e211c0f71c8b11ec71cae167d4e2fb1ec8dee9a87.437aa611e89f6fc6675a049d2b5545390adbc617e7d655286421c191d2be2791
loading file https://huggingface.co/bert-large-cased-whole-word-masking-finetuned-squad/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/7e7140ff927e58a37a0862cd3dc4e2873c713af14eaf32a602d99

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

In [ ]:
results_translate_test_bert_large = compute_results(langs_translate_test, split)
print(results_translate_test_bert_large)

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6187
  Batch size = 16


Post-processing 5335 example predictions split into 6187 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5010
  Batch size = 16


Post-processing 4517 example predictions split into 5010 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5569
  Batch size = 16


Post-processing 4918 example predictions split into 5569 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 28.922211808809745, 'f1': 52.65882141015699}, 'translate-test.de': {'exact_match': 37.148549922514945, 'f1': 56.67746913086446}, 'translate-test.vi': {'exact_match': 34.74067333939946, 'f1': 56.71578980297325}, 'translate-test.zh': {'exact_match': 27.79832587113101, 'f1': 50.13426121040247}, 'translate-test.es': {'exact_match': 45.19322292023605, 'f1': 67.14829009899658}, 'translate-test.hi': {'exact_match': 33.81455876372509, 'f1': 55.20335337137669}}


In [ ]:
df_results_translate_test_bert_large = results_df(results_translate_test_bert_large, "Translate-test BERT Large")
df_results_translate_test_bert_large.to_csv("results/mlqa/results_translate_test_bert_large.csv")
df_results_translate_test_bert_large

lang  F1_Translate-test BERT Large  \
0  translate-test.ar                         52.66   
1  translate-test.de                         56.68   
2  translate-test.vi                         56.72   
3  translate-test.zh                         50.13   
4  translate-test.es                         67.15   
5  translate-test.hi                         55.20   
6                avg                         56.42   

   EM_Translate-test BERT Large  
0                         28.92  
1                         37.15  
2                         34.74  
3                         27.80  
4                         45.19  
5                         33.81  
6                         34.60

## Translate Test RoBERTa

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we use a monolingual RoBERTa model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "thatdramebaazguy/roberta-base-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="roberta-base-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpl3qrnei0


Downloading:   0%|          | 0.00/720 [00:00<?, ?B/s]

storing https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/892dedc3d4dc51337f07712ae60bee9d35540607c674cf14c1e8fa759c8044f6.143a3b91b00882c22e382aa9dce198fca4876a0147d4208940720f26038eecea
creating metadata file for /root/.cache/huggingface/transformers/892dedc3d4dc51337f07712ae60bee9d35540607c674cf14c1e8fa759c8044f6.143a3b91b00882c22e382aa9dce198fca4876a0147d4208940720f26038eecea
loading configuration file https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/892dedc3d4dc51337f07712ae60bee9d35540607c674cf14c1e8fa759c8044f6.143a3b91b00882c22e382aa9dce198fca4876a0147d4208940720f26038eecea
Model config RobertaConfig {
  "_name_or_path": "thatdramebaazguy/roberta-base-squad",
  "architectures": [
    "RobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "

Downloading:   0%|          | 0.00/473M [00:00<?, ?B/s]

storing https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/eae6ec0ceba7122f93f8ba10ea14828355c6db5ccbe45329df98c66acc6dec1c.e2c6aeaa07a1eaf01009558b402d71dc19744520a98718fc20f5d6777489a1c0
creating metadata file for /root/.cache/huggingface/transformers/eae6ec0ceba7122f93f8ba10ea14828355c6db5ccbe45329df98c66acc6dec1c.e2c6aeaa07a1eaf01009558b402d71dc19744520a98718fc20f5d6777489a1c0
loading weights file https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/eae6ec0ceba7122f93f8ba10ea14828355c6db5ccbe45329df98c66acc6dec1c.e2c6aeaa07a1eaf01009558b402d71dc19744520a98718fc20f5d6777489a1c0
All model checkpoint weights were used when initializing RobertaForQuestionAnswering.

All the weights of RobertaForQuestionAnswering were initialized from the model checkpoint at thatdramebaazguy/roberta-base-squad.
If your task is s

...

storing https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/vocab.json in cache at /root/.cache/huggingface/transformers/1fe6670fd1703bab634d459d85ba622bc85238b2ddd5e4a959e3e8ae4236db44.bfdcc444ff249bca1a95ca170ec350b442f81804d7df3a95a2252217574121d7
creating metadata file for /root/.cache/huggingface/transformers/1fe6670fd1703bab634d459d85ba622bc85238b2ddd5e4a959e3e8ae4236db44.bfdcc444ff249bca1a95ca170ec350b442f81804d7df3a95a2252217574121d7
https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/merges.txt not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp94zxtzxm


Downloading:   0%|          | 0.00/446k [00:00<?, ?B/s]

storing https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/merges.txt in cache at /root/.cache/huggingface/transformers/52729906e4dae69dd2c4542bd269069500d1eff2e5ee45010976e928b6c7e42c.f5b91da9e34259b8f4d88dbc97c740667a0e8430b96314460cdb04e86d4fc435
creating metadata file for /root/.cache/huggingface/transformers/52729906e4dae69dd2c4542bd269069500d1eff2e5ee45010976e928b6c7e42c.f5b91da9e34259b8f4d88dbc97c740667a0e8430b96314460cdb04e86d4fc435
https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpj_mfs115


Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

storing https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/bc9c87f318c0ab6db507f08aa6e3e125ba1565b61fdbbf2f8a321dc8a4ad5ad5.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
creating metadata file for /root/.cache/huggingface/transformers/bc9c87f318c0ab6db507f08aa6e3e125ba1565b61fdbbf2f8a321dc8a4ad5ad5.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
loading file https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/vocab.json from cache at /root/.cache/huggingface/transformers/1fe6670fd1703bab634d459d85ba622bc85238b2ddd5e4a959e3e8ae4236db44.bfdcc444ff249bca1a95ca170ec350b442f81804d7df3a95a2252217574121d7
loading file https://huggingface.co/thatdramebaazguy/roberta-base-squad/resolve/main/merges.txt from cache at /root/.cache/huggingface/transformers/52729906e4dae69dd2c4542bd269069500d1eff2e5ee45010976e928b6c7e42c.f5b91da9e34259b8f4d88dbc97c740

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_roberta = compute_results(langs_translate_test, split)
print(results_translate_test_roberta)

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6126
  Batch size = 16


Post-processing 5335 example predictions split into 6126 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 4988
  Batch size = 16


Post-processing 4517 example predictions split into 4988 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5569
  Batch size = 16


Post-processing 4918 example predictions split into 5569 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 27.628865979381445, 'f1': 51.38025016759656}, 'translate-test.de': {'exact_match': 34.09342483949524, 'f1': 54.12628800304434}, 'translate-test.vi': {'exact_match': 32.39308462238399, 'f1': 54.02919611641149}, 'translate-test.zh': {'exact_match': 25.228732723379405, 'f1': 47.6495109216957}, 'translate-test.es': {'exact_match': 43.44184275652008, 'f1': 66.02058063225972}, 'translate-test.hi': {'exact_match': 30.98820658804392, 'f1': 52.33958690154472}}


In [ ]:
df_results_translate_test_roberta = results_df(results_translate_test_roberta, "Translate-test RoBERTa")
df_results_translate_test_roberta.to_csv("results/mlqa/results_translate_test_roberta.csv")
df_results_translate_test_roberta

lang  F1_Translate-test RoBERTa  EM_Translate-test RoBERTa
0  translate-test.ar                      51.38                      27.63
1  translate-test.de                      54.13                      34.09
2  translate-test.vi                      54.03                      32.39
3  translate-test.zh                      47.65                      25.23
4  translate-test.es                      66.02                      43.44
5  translate-test.hi                      52.34                      30.99
6                avg                      54.26                      32.30

## Translate Test RoBERTa-large

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we use a monolingual RoBERTa-large model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "csarron/roberta-large-squad-v1"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="roberta-large-squad-v1",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpze71lcm9


Downloading:   0%|          | 0.00/526 [00:00<?, ?B/s]

storing https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/0fc041ca661ebb7473123e9722819c48e27f9a83aedf13e1150435275cc21bdd.e59dc72a749f921962e2e724ff292de7eb1b9902723153972b2069e8847ff4f0
creating metadata file for /root/.cache/huggingface/transformers/0fc041ca661ebb7473123e9722819c48e27f9a83aedf13e1150435275cc21bdd.e59dc72a749f921962e2e724ff292de7eb1b9902723153972b2069e8847ff4f0
loading configuration file https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/0fc041ca661ebb7473123e9722819c48e27f9a83aedf13e1150435275cc21bdd.e59dc72a749f921962e2e724ff292de7eb1b9902723153972b2069e8847ff4f0
Model config RobertaConfig {
  "_name_or_path": "csarron/roberta-large-squad-v1",
  "architectures": [
    "RobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id": 

Downloading:   0%|          | 0.00/1.32G [00:00<?, ?B/s]

storing https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/935ac7e3a963d7bbb378084e7fd258dff35107d1f2adf0330552dccd9d042b67.dcb0046418df96c9fb3968477de7cd19a4f6ccb9b4796bca32743ccf081b9859
creating metadata file for /root/.cache/huggingface/transformers/935ac7e3a963d7bbb378084e7fd258dff35107d1f2adf0330552dccd9d042b67.dcb0046418df96c9fb3968477de7cd19a4f6ccb9b4796bca32743ccf081b9859
loading weights file https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/935ac7e3a963d7bbb378084e7fd258dff35107d1f2adf0330552dccd9d042b67.dcb0046418df96c9fb3968477de7cd19a4f6ccb9b4796bca32743ccf081b9859
All model checkpoint weights were used when initializing RobertaForQuestionAnswering.

All the weights of RobertaForQuestionAnswering were initialized from the model checkpoint at csarron/roberta-large-squad-v1.
If your task is similar to the t

...

storing https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/vocab.json in cache at /root/.cache/huggingface/transformers/5e33c3e3fc394fe42529078e25b17308c41253999ae658832e1d00c1e35e2f23.647b4548b6d9ea817e82e7a9231a320231a1c9ea24053cc9e758f3fe68216f05
creating metadata file for /root/.cache/huggingface/transformers/5e33c3e3fc394fe42529078e25b17308c41253999ae658832e1d00c1e35e2f23.647b4548b6d9ea817e82e7a9231a320231a1c9ea24053cc9e758f3fe68216f05
https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/merges.txt not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpwgcoou3l


Downloading:   0%|          | 0.00/446k [00:00<?, ?B/s]

storing https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/merges.txt in cache at /root/.cache/huggingface/transformers/48047eb6f8b799c467d0f97316aa9b6e520be6ace95983203d421834eb0c0b54.5d12962c5ee615a4c803841266e9c3be9a691a924f72d395d3a6c6c81157788b
creating metadata file for /root/.cache/huggingface/transformers/48047eb6f8b799c467d0f97316aa9b6e520be6ace95983203d421834eb0c0b54.5d12962c5ee615a4c803841266e9c3be9a691a924f72d395d3a6c6c81157788b
https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp3ee6ehpd


Downloading:   0%|          | 0.00/772 [00:00<?, ?B/s]

storing https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/030f51904149258d64958d23a91fbc76c0fe866b3a4c2605c337b5adbb330e3e.cb2244924ab24d706b02fd7fcedaea4531566537687a539ebb94db511fd122a0
creating metadata file for /root/.cache/huggingface/transformers/030f51904149258d64958d23a91fbc76c0fe866b3a4c2605c337b5adbb330e3e.cb2244924ab24d706b02fd7fcedaea4531566537687a539ebb94db511fd122a0
loading file https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/vocab.json from cache at /root/.cache/huggingface/transformers/5e33c3e3fc394fe42529078e25b17308c41253999ae658832e1d00c1e35e2f23.647b4548b6d9ea817e82e7a9231a320231a1c9ea24053cc9e758f3fe68216f05
loading file https://huggingface.co/csarron/roberta-large-squad-v1/resolve/main/merges.txt from cache at /root/.cache/huggingface/transformers/48047eb6f8b799c467d0f97316aa9b6e520be6ace95983203d421834eb0c0b54.5d12962c5ee615a4c803841266e9c3be9a691a924f72d

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_roberta_large = compute_results(langs_translate_test, split)
print(results_translate_test_roberta_large)

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6126
  Batch size = 16


Post-processing 5335 example predictions split into 6126 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 4988
  Batch size = 16


Post-processing 4517 example predictions split into 4988 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `RobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `RobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5569
  Batch size = 16


Post-processing 4918 example predictions split into 5569 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 29.44704779756326, 'f1': 53.67646362931118}, 'translate-test.de': {'exact_match': 37.94553907460704, 'f1': 57.43215793599518}, 'translate-test.vi': {'exact_match': 34.8680618744313, 'f1': 56.31776481607472}, 'translate-test.zh': {'exact_match': 27.739926026863927, 'f1': 50.579167184195526}, 'translate-test.es': {'exact_match': 45.859508852084524, 'f1': 67.96331137713167}, 'translate-test.hi': {'exact_match': 33.89589263928426, 'f1': 55.65840481399972}}


In [ ]:
df_results_translate_test_roberta_large = results_df(results_translate_test_roberta_large, "Translate-test RoBERTa Large")
df_results_translate_test_roberta_large.to_csv("results/mlqa/results_translate_test_roberta_large.csv")
df_results_translate_test_roberta_large

lang  F1_Translate-test RoBERTa Large  \
0  translate-test.ar                            53.68   
1  translate-test.de                            57.43   
2  translate-test.vi                            56.32   
3  translate-test.zh                            50.58   
4  translate-test.es                            67.96   
5  translate-test.hi                            55.66   
6                avg                            56.94   

   EM_Translate-test RoBERTa Large  
0                            29.45  
1                            37.95  
2                            34.87  
3                            27.74  
4                            45.86  
5                            33.90  
6                            34.96

## Translate Test mBERT

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we  use mBERT, but we could also use a monolingual model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "salti/bert-base-multilingual-cased-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bert-base-multilingual-cased-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpsnr08ejf


Downloading:   0%|          | 0.00/822 [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
creating metadata file for /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
loading configuration file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
Model config BertConfig {
  "_name_or_path": "salti/bert-base-multilingual-cased-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_d

Downloading:   0%|          | 0.00/676M [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
creating metadata file for /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
loading weights file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/9f54849aca742a855728dc8a74c1a733627678a2e8c7a97ba60e2b318ad1438a.b9c031b09975cb84030a5da7731e0b35844cbf7eed5f7ddc0dc0704ba6cc5802
All model checkpoint weights were used when initializing BertForQuestionAnswering.

All the weights of BertForQuestionAnswering were initialized from the model checkpoint at salti/bert-base-multilingual-c

...

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/834c4d17cccdc848e5ac1e4978b371d9d3afa3bb371fe8f6be85119e3a0ea885.c60f034cf5bf819518a0170960ddb62b4576fa3d01e9021876b801600cbb6f42
creating metadata file for /root/.cache/huggingface/transformers/834c4d17cccdc848e5ac1e4978b371d9d3afa3bb371fe8f6be85119e3a0ea885.c60f034cf5bf819518a0170960ddb62b4576fa3d01e9021876b801600cbb6f42
loading configuration file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/1df6572a9ae2fd1152d4fa4e3b9d30e0d303c69cb87d5b8401ef5cb032016bef.aa91fcc51e661ddbf70fda4906759b1d8178a512385633adf5d0db934ae1e333
Model config BertConfig {
  "_name_or_path": "salti/bert-base-multilingual-cased-finetuned-squad",
  "architectures": [
    "BertForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "cl

Downloading:   0%|          | 0.00/972k [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/vocab.txt in cache at /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
creating metadata file for /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp2i51wegf


Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

storing https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/33bece2c5789380abddaab5941fb528198297c167ddfa9547ab37dd92f940b55.dd8bd9bfd3664b530ea4e645105f557769387b3da9f79bdb55ed556bdd80611d
creating metadata file for /root/.cache/huggingface/transformers/33bece2c5789380abddaab5941fb528198297c167ddfa9547ab37dd92f940b55.dd8bd9bfd3664b530ea4e645105f557769387b3da9f79bdb55ed556bdd80611d
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/vocab.txt from cache at /root/.cache/huggingface/transformers/f4a09a359df2eb92d135ea2d1092b9f0f3388951f8612fd97e9b071eaa3c3c98.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned-squad/resolve/main/tokenizer.json from cache at None
loading file https://huggingface.co/salti/bert-base-multilingual-cased-finetuned

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_mbert = compute_results(langs_translate_test, split)
print(results_translate_test_mbert)

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6239
  Batch size = 16


Post-processing 5335 example predictions split into 6239 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5025
  Batch size = 16


Post-processing 4517 example predictions split into 5025 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `BertForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `BertForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5573
  Batch size = 16


Post-processing 4918 example predictions split into 5573 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 26.991565135895033, 'f1': 49.47955999968681}, 'translate-test.de': {'exact_match': 34.823998228913, 'f1': 53.60873389555618}, 'translate-test.vi': {'exact_match': 32.010919017288444, 'f1': 53.42900563300508}, 'translate-test.zh': {'exact_match': 24.489001362663032, 'f1': 45.930361811963955}, 'translate-test.es': {'exact_match': 43.023034456501044, 'f1': 64.28367561464714}, 'translate-test.hi': {'exact_match': 31.23220821472143, 'f1': 51.89148534618668}}


In [ ]:
df_results_translate_test_mbert = results_df(results_translate_test_mbert, "Translate-test mBERT")
df_results_translate_test_mbert.to_csv("results/mlqa/results_translate_test_mbert.csv")
df_results_translate_test_mbert

lang  F1_Translate-test mBERT  EM_Translate-test mBERT
0  translate-test.ar                    49.48                    26.99
1  translate-test.de                    53.61                    34.82
2  translate-test.vi                    53.43                    32.01
3  translate-test.zh                    45.93                    24.49
4  translate-test.es                    64.28                    43.02
5  translate-test.hi                    51.89                    31.23
6                avg                    53.10                    32.10

## Translate Test XLM-R

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we  use XLM-R, but we could also use a monolingual model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "vanichandna/xlm-roberta-finetuned-squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name,from_tf=True)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-finetuned-squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpqrd6y9qg


Downloading:   0%|          | 0.00/688 [00:00<?, ?B/s]

storing https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/6e9fab04c4168068e4162152496d68d0594b8a838953657e9234b70b2c4932fb.b04b4828cf6cfcbbcba34b7e4fc29fe9a0563001f3cedda0f9cf6487875eae92
creating metadata file for /root/.cache/huggingface/transformers/6e9fab04c4168068e4162152496d68d0594b8a838953657e9234b70b2c4932fb.b04b4828cf6cfcbbcba34b7e4fc29fe9a0563001f3cedda0f9cf6487875eae92
loading configuration file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/6e9fab04c4168068e4162152496d68d0594b8a838953657e9234b70b2c4932fb.b04b4828cf6cfcbbcba34b7e4fc29fe9a0563001f3cedda0f9cf6487875eae92
Model config XLMRobertaConfig {
  "_name_or_path": "vanichandna/xlm-roberta-finetuned-squad",
  "architectures": [
    "XLMRobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_d

Downloading:   0%|          | 0.00/1.03G [00:00<?, ?B/s]

storing https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tf_model.h5 in cache at /root/.cache/huggingface/transformers/40231dec3bc81ec27bf1027247098bd684738dffa5f2296b2cad573879d0c229.fdcf91f65f36389325caf97398f95d17232f926dca8f8ecac72019c5ca36ba9d.h5
creating metadata file for /root/.cache/huggingface/transformers/40231dec3bc81ec27bf1027247098bd684738dffa5f2296b2cad573879d0c229.fdcf91f65f36389325caf97398f95d17232f926dca8f8ecac72019c5ca36ba9d.h5
loading weights file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tf_model.h5 from cache at /root/.cache/huggingface/transformers/40231dec3bc81ec27bf1027247098bd684738dffa5f2296b2cad573879d0c229.fdcf91f65f36389325caf97398f95d17232f926dca8f8ecac72019c5ca36ba9d.h5
Loading TensorFlow weights from /root/.cache/huggingface/transformers/40231dec3bc81ec27bf1027247098bd684738dffa5f2296b2cad573879d0c229.fdcf91f65f36389325caf97398f95d17232f926dca8f8ecac72019c5ca36ba9d.h5
All TF 2.0 model weights w

...

storing https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/14a0caad62ab9246eaaf3d48369dcfa9230e8c7a75c21a5a5b984e9b681a780b.b36482fbec4a714d3cfec99e0b05f4fdeec9e759090a78aed5597583a8b4783d
creating metadata file for /root/.cache/huggingface/transformers/14a0caad62ab9246eaaf3d48369dcfa9230e8c7a75c21a5a5b984e9b681a780b.b36482fbec4a714d3cfec99e0b05f4fdeec9e759090a78aed5597583a8b4783d
https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmphsij3mmd


Downloading:   0%|          | 0.00/16.3M [00:00<?, ?B/s]

storing https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/7f7f92d02ee98c92db3e0ef5445a40b8301c4206d4df0adc2bbb55b109b17dc3.d9915425c8f75472760a4bb40b4d5d0b3ab357a1b00aaf7917cda68403cbc936
creating metadata file for /root/.cache/huggingface/transformers/7f7f92d02ee98c92db3e0ef5445a40b8301c4206d4df0adc2bbb55b109b17dc3.d9915425c8f75472760a4bb40b4d5d0b3ab357a1b00aaf7917cda68403cbc936
https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpk3b4qqu3


Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

storing https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/21e94506b48b2fcd8bf2ffb7d2216e68cb34dd50b493e0cdbffbb6c97efd961b.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
creating metadata file for /root/.cache/huggingface/transformers/21e94506b48b2fcd8bf2ffb7d2216e68cb34dd50b493e0cdbffbb6c97efd961b.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
loading file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/sentencepiece.bpe.model from cache at None
loading file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/7f7f92d02ee98c92db3e0ef5445a40b8301c4206d4df0adc2bbb55b109b17dc3.d9915425c8f75472760a4bb40b4d5d0b3ab357a1b00aaf7917cda68403cbc936
loading file https://huggingface.co/vanichandna/xlm-roberta-finetuned-squad/resolve/main/added_toke

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_xlm_r = compute_results(langs_translate_test, split)
print(results_translate_test_xlm_r)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6365
  Batch size = 16


Post-processing 5335 example predictions split into 6365 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5109
  Batch size = 16


Post-processing 4517 example predictions split into 5109 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5639
  Batch size = 16


Post-processing 4918 example predictions split into 5639 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 27.722586691658858, 'f1': 50.396355001537636}, 'translate-test.de': {'exact_match': 34.89041399158734, 'f1': 53.569903233376195}, 'translate-test.vi': {'exact_match': 33.37579617834395, 'f1': 54.18176084854039}, 'translate-test.zh': {'exact_match': 26.104730387385633, 'f1': 47.6635059820223}, 'translate-test.es': {'exact_match': 43.023034456501044, 'f1': 64.77360448959764}, 'translate-test.hi': {'exact_match': 32.04554697031313, 'f1': 52.756969911141226}}


In [ ]:
df_results_translate_test_xlm_r = results_df(results_translate_test_xlm_r, "Translate-test XLM-R")
df_results_translate_test_xlm_r.to_csv("results/mlqa/results_translate_test_xlm_r.csv")
df_results_translate_test_xlm_r

lang  F1_Translate-test XLM-R  EM_Translate-test XLM-R
0  translate-test.ar                    50.40                    27.72
1  translate-test.de                    53.57                    34.89
2  translate-test.vi                    54.18                    33.38
3  translate-test.zh                    47.66                    26.10
4  translate-test.es                    64.77                    43.02
5  translate-test.hi                    52.76                    32.05
6                avg                    53.89                    32.86

## Translate Test XLM-R-large

We use the model fine-tuned on SQuAD and evaluate it on test data that we translated from the target language to English. In this case we use XLM-R-large, but we could also use a monolingual model, because we only evaluate on English data.

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "Palak/xlm-roberta-large_squad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-large_squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

loading configuration file https://huggingface.co/Palak/xlm-roberta-large_squad/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/15ba31e9d5d227c3e7514429b9e154b4dd9fa20dc6634e2aa859a6570580ab8a.e0ee6561aeb1e6c81ca8555d0aed71ddc7b312c694416a29b2dd0b16df13a0b3
Model config XLMRobertaConfig {
  "_name_or_path": "Palak/xlm-roberta-large_squad",
  "architectures": [
    "XLMRobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": null,
  "eos_token_id": 2,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 1024,
  "initializer_range": 0.02,
  "intermediate_size": 4096,
  "layer_norm_eps": 1e-05,
  "max_position_embeddings": 514,
  "model_type": "xlm-roberta",
  "num_attention_heads": 16,
  "num_hidden_layers": 24,
  "output_past": true,
  "pad_token_id": 1,
  "position_embedding_type": "absolute",
  "torch_dtype": "float32",
  "transformers_version": "4.19.2",
  "type_vocab_size": 1,

In [ ]:
split = "test"
map_datasets(langs_translate_test, split, prepare_validation_features)

Loading cached processed dataset at /root/.cache/huggingface/datasets/mlqa/mlqa-translate-test.ar/1.0.0/224fde9ea61350ffb013e4beff31d44c6e125ce82c3aa4af70298eceabc8f7f7/cache-aaa4522b310f3ccd.arrow
Loading cached processed dataset at /root/.cache/huggingface/datasets/mlqa/mlqa-translate-test.de/1.0.0/224fde9ea61350ffb013e4beff31d44c6e125ce82c3aa4af70298eceabc8f7f7/cache-f6baa9880ba3f1c9.arrow


  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
results_translate_test_xlm_r_large = compute_results(langs_translate_test, split)
print(results_translate_test_xlm_r_large)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6365
  Batch size = 16


Post-processing 5335 example predictions split into 6365 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5109
  Batch size = 16


Post-processing 4517 example predictions split into 5109 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5639
  Batch size = 16


Post-processing 4918 example predictions split into 5639 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'translate-test.ar': {'exact_match': 29.203373945641985, 'f1': 53.14333435180998}, 'translate-test.de': {'exact_match': 37.436351560770426, 'f1': 56.56193943869914}, 'translate-test.vi': {'exact_match': 34.52229299363057, 'f1': 56.606263676988995}, 'translate-test.zh': {'exact_match': 27.603659723574072, 'f1': 49.98454027712602}, 'translate-test.es': {'exact_match': 46.54483152484295, 'f1': 68.56577512540538}, 'translate-test.hi': {'exact_match': 34.50589670597804, 'f1': 55.57006347649452}}


In [ ]:
df_results_translate_test_xlm_r_large = results_df(results_translate_test_xlm_r_large, "Translate-test XLM-R Large")
df_results_translate_test_xlm_r_large.to_csv("results/mlqa/results_translate_test_xlm_r_large.csv")
df_results_translate_test_xlm_r_large

lang  F1_Translate-test XLM-R Large  \
0  translate-test.ar                          53.14   
1  translate-test.de                          56.56   
2  translate-test.vi                          56.61   
3  translate-test.zh                          49.98   
4  translate-test.es                          68.57   
5  translate-test.hi                          55.57   
6                avg                          56.74   

   EM_Translate-test XLM-R Large  
0                          29.20  
1                          37.44  
2                          34.52  
3                          27.60  
4                          46.54  
5                          34.51  
6                          34.97

## Translate Train Es mBERT

For many language pairs, a MT model may be available, which can be used to obtain data in the target language. To evaluate the impact of using such data, we translate the English training data into the target language using our MT system. We then fine-tune mBERT on the translated data. We must align answer spans in the source and target language for the QA tasks. We use data that was already translated to save time.

Now that our data is ready for training, we can download the pretrained model and fine-tune it. Since our task is question answering, we use the `AutoModelForQuestionAnswering` class. Like with the tokenizer, the `from_pretrained` method will download and cache the model for us:

In [ ]:
from transformers import AutoModelForQuestionAnswering, TrainingArguments, Trainer

model_name = "bert-base-multilingual-cased"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

batch_size = 16

training_args = TrainingArguments(
    output_dir="bert-base-multilingual-cased-squad-es",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
    push_to_hub=True
)

https://huggingface.co/bert-base-multilingual-cased/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpiqij3gtd


Downloading:   0%|          | 0.00/625 [00:00<?, ?B/s]

storing https://huggingface.co/bert-base-multilingual-cased/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/6c4a5d81a58c9791cdf76a09bce1b5abfb9cf958aebada51200f4515403e5d08.0fe59f3f4f1335dadeb4bce8b8146199d9083512b50d07323c1c319f96df450c
creating metadata file for /root/.cache/huggingface/transformers/6c4a5d81a58c9791cdf76a09bce1b5abfb9cf958aebada51200f4515403e5d08.0fe59f3f4f1335dadeb4bce8b8146199d9083512b50d07323c1c319f96df450c
loading configuration file https://huggingface.co/bert-base-multilingual-cased/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/6c4a5d81a58c9791cdf76a09bce1b5abfb9cf958aebada51200f4515403e5d08.0fe59f3f4f1335dadeb4bce8b8146199d9083512b50d07323c1c319f96df450c
Model config BertConfig {
  "_name_or_path": "bert-base-multilingual-cased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "hidden_act": "gelu",
  "hidde

Downloading:   0%|          | 0.00/681M [00:00<?, ?B/s]

storing https://huggingface.co/bert-base-multilingual-cased/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/0a3fd51713dcbb4def175c7f85bddc995d5976ce1dde327f99104e4d33069f17.aa7be4c79d76f4066d9b354496ea477c9ee39c5d889156dd1efb680643c2b052
creating metadata file for /root/.cache/huggingface/transformers/0a3fd51713dcbb4def175c7f85bddc995d5976ce1dde327f99104e4d33069f17.aa7be4c79d76f4066d9b354496ea477c9ee39c5d889156dd1efb680643c2b052
loading weights file https://huggingface.co/bert-base-multilingual-cased/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/0a3fd51713dcbb4def175c7f85bddc995d5976ce1dde327f99104e4d33069f17.aa7be4c79d76f4066d9b354496ea477c9ee39c5d889156dd1efb680643c2b052
Some weights of the model checkpoint at bert-base-multilingual-cased were not used when initializing BertForQuestionAnswering: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', '

...

storing https://huggingface.co/bert-base-multilingual-cased/resolve/main/tokenizer_config.json in cache at /root/.cache/huggingface/transformers/f55e7a2ad4f8d0fff2733b3f79777e1e99247f2e4583703e92ce74453af8c235.ec5c189f89475aac7d8cbd243960a0655cfadc3d0474da8ff2ed0bf1699c2a5f
creating metadata file for /root/.cache/huggingface/transformers/f55e7a2ad4f8d0fff2733b3f79777e1e99247f2e4583703e92ce74453af8c235.ec5c189f89475aac7d8cbd243960a0655cfadc3d0474da8ff2ed0bf1699c2a5f
loading configuration file https://huggingface.co/bert-base-multilingual-cased/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/6c4a5d81a58c9791cdf76a09bce1b5abfb9cf958aebada51200f4515403e5d08.0fe59f3f4f1335dadeb4bce8b8146199d9083512b50d07323c1c319f96df450c
Model config BertConfig {
  "_name_or_path": "bert-base-multilingual-cased",
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "classifier_dropout": null,
  "directionality": "bidi",
  "hidden_act": "gelu"

Downloading:   0%|          | 0.00/972k [00:00<?, ?B/s]

storing https://huggingface.co/bert-base-multilingual-cased/resolve/main/vocab.txt in cache at /root/.cache/huggingface/transformers/eff018e45de5364a8368df1f2df3461d506e2a111e9dd50af1fae061cd460ead.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
creating metadata file for /root/.cache/huggingface/transformers/eff018e45de5364a8368df1f2df3461d506e2a111e9dd50af1fae061cd460ead.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
https://huggingface.co/bert-base-multilingual-cased/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpcu096rqh


Downloading:   0%|          | 0.00/1.87M [00:00<?, ?B/s]

storing https://huggingface.co/bert-base-multilingual-cased/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/46880f3b0081fda494a4e15b05787692aa4c1e21e0ff2428ba8b14d4eda0784d.b33e51591f94f17c238ee9b1fac75b96ff2678cbaed6e108feadb3449d18dc24
creating metadata file for /root/.cache/huggingface/transformers/46880f3b0081fda494a4e15b05787692aa4c1e21e0ff2428ba8b14d4eda0784d.b33e51591f94f17c238ee9b1fac75b96ff2678cbaed6e108feadb3449d18dc24
loading file https://huggingface.co/bert-base-multilingual-cased/resolve/main/vocab.txt from cache at /root/.cache/huggingface/transformers/eff018e45de5364a8368df1f2df3461d506e2a111e9dd50af1fae061cd460ead.6c5b6600e968f4b5e08c86d8891ea99e51537fc2bf251435fb46922e8f7a7b29
loading file https://huggingface.co/bert-base-multilingual-cased/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/46880f3b0081fda494a4e15b05787692aa4c1e21e0ff2428ba8b14d4eda0784d.b33e51591f94f17c238ee9b1fac75b96ff2678cbaed6e108feadb3449

Use 🤗 Datasets map function to apply the preprocessing function over the entire dataset. You can speed up the map function by setting `batched=True` to process multiple elements of the dataset at once. Remove the columns you don’t need.

In [ ]:
lang = ["translate-train.es"]

split = "train"
map_datasets(lang, split, prepare_train_features)

split = "validation"
map_datasets(lang, split, prepare_train_features)

  0%|          | 0/82 [00:00<?, ?ba/s]

  0%|          | 0/11 [00:00<?, ?ba/s]

In [ ]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=mlqa_prep["translate-train.es"]["train"],
    eval_dataset=mlqa_prep["translate-train.es"]["validation"],
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
# trainer.train()

In [ ]:
split = "test"
map_datasets(langs_test, split, prepare_validation_features)

In [ ]:
split = "test"
results_translate_train_es_mbert = compute_results(langs_test, split)
print(results_translate_train_es_mbert)

In [ ]:
df_results_translate_train_es_mbert = results_df(results_translate_train_es_mbert, "Translate-train es mBERT")
df_results_translate_train_es_mbert.to_csv("results/mlqa/results_translate_train_es_mbert.csv")
df_results_translate_train_es_mbert

In [ ]:
trainer.push_to_hub()

## Translate Train Es XLM-R

For many language pairs, a MT model may be available, which can be used to obtain data in the target language. To evaluate the impact of using such data, we translate the English training data into the target language using our MT system. We use a XLM-R model that has already been finetuned to save time.

Now that our data is ready for training, we can download the pretrained model and fine-tune it. Since our task is question answering, we use the `AutoModelForQuestionAnswering` class. Like with the tokenizer, the `from_pretrained` method will download and cache the model for us:

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "saattrupdan/xlmr-base-texas-squad-es"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlmr-base-texas-squad-es",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/config.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmphyriq57u


Downloading:   0%|          | 0.00/716 [00:00<?, ?B/s]

storing https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/config.json in cache at /root/.cache/huggingface/transformers/faf74a33d110680ea7f72791fa918036c0fd9edbcbdbf36af3bde7c86b23a8f2.b749a309a5febb0957ff5acc5d4f5534d14f38569553b954c37647de7ea10ae4
creating metadata file for /root/.cache/huggingface/transformers/faf74a33d110680ea7f72791fa918036c0fd9edbcbdbf36af3bde7c86b23a8f2.b749a309a5febb0957ff5acc5d4f5534d14f38569553b954c37647de7ea10ae4
loading configuration file https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/config.json from cache at /root/.cache/huggingface/transformers/faf74a33d110680ea7f72791fa918036c0fd9edbcbdbf36af3bde7c86b23a8f2.b749a309a5febb0957ff5acc5d4f5534d14f38569553b954c37647de7ea10ae4
Model config XLMRobertaConfig {
  "_name_or_path": "saattrupdan/xlmr-base-texas-squad-es",
  "architectures": [
    "XLMRobertaForQuestionAnswering"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bos_token_id": 0,
  "classifier_dropout": 

Downloading:   0%|          | 0.00/1.03G [00:00<?, ?B/s]

storing https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/pytorch_model.bin in cache at /root/.cache/huggingface/transformers/acdf22ff03faa9cd992d27a19088abdc9f28a3b4e1e40a14e98cfcb0b18c1403.d1cb5eddd332add5df96171f7f759027748f6b03de7b4fdd45f72ebf349e9eb3
creating metadata file for /root/.cache/huggingface/transformers/acdf22ff03faa9cd992d27a19088abdc9f28a3b4e1e40a14e98cfcb0b18c1403.d1cb5eddd332add5df96171f7f759027748f6b03de7b4fdd45f72ebf349e9eb3
loading weights file https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/pytorch_model.bin from cache at /root/.cache/huggingface/transformers/acdf22ff03faa9cd992d27a19088abdc9f28a3b4e1e40a14e98cfcb0b18c1403.d1cb5eddd332add5df96171f7f759027748f6b03de7b4fdd45f72ebf349e9eb3
All model checkpoint weights were used when initializing XLMRobertaForQuestionAnswering.

All the weights of XLMRobertaForQuestionAnswering were initialized from the model checkpoint at saattrupdan/xlmr-base-texas-squad-es.
If your 

...

storing https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/sentencepiece.bpe.model in cache at /root/.cache/huggingface/transformers/e70140c9e0682f255072dc32b137ae3cde1808241a5359b356fa10413d32a677.71e50b08dbe7e5375398e165096cacc3d2086119d6a449364490da6908de655e
creating metadata file for /root/.cache/huggingface/transformers/e70140c9e0682f255072dc32b137ae3cde1808241a5359b356fa10413d32a677.71e50b08dbe7e5375398e165096cacc3d2086119d6a449364490da6908de655e
https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/tokenizer.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmpp8jnda23


Downloading:   0%|          | 0.00/8.66M [00:00<?, ?B/s]

storing https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/tokenizer.json in cache at /root/.cache/huggingface/transformers/6aa7bc2ebebd8aec9f0d822224378677812644178ecff3c50ceddf15ed84427c.2dedbd3aa2bb53e8e26ed0125daf18f6d4aeeeeb98252d7ce59b3a63d810a963
creating metadata file for /root/.cache/huggingface/transformers/6aa7bc2ebebd8aec9f0d822224378677812644178ecff3c50ceddf15ed84427c.2dedbd3aa2bb53e8e26ed0125daf18f6d4aeeeeb98252d7ce59b3a63d810a963
https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/special_tokens_map.json not found in cache or force_download set to True, downloading to /root/.cache/huggingface/transformers/tmp38tgid8q


Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

storing https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/special_tokens_map.json in cache at /root/.cache/huggingface/transformers/f06ef5b71fd7eb7e035d0f645a260e1b7933933ff5438715bc96d41446ac6db1.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
creating metadata file for /root/.cache/huggingface/transformers/f06ef5b71fd7eb7e035d0f645a260e1b7933933ff5438715bc96d41446ac6db1.a11ebb04664c067c8fe5ef8f8068b0f721263414a26058692f7b2e4ba2a1b342
loading file https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/sentencepiece.bpe.model from cache at /root/.cache/huggingface/transformers/e70140c9e0682f255072dc32b137ae3cde1808241a5359b356fa10413d32a677.71e50b08dbe7e5375398e165096cacc3d2086119d6a449364490da6908de655e
loading file https://huggingface.co/saattrupdan/xlmr-base-texas-squad-es/resolve/main/tokenizer.json from cache at /root/.cache/huggingface/transformers/6aa7bc2ebebd8aec9f0d822224378677812644178ecff3c50ceddf15ed84427c.2dedbd3aa2

In [ ]:
split = "test"
map_datasets(langs_translate_train, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/12 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [ ]:
split = "test"
results_translate_train_es_xlm_r = compute_results(langs_translate_train, split)
print(results_translate_train_es_xlm_r)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6810
  Batch size = 16


Post-processing 5335 example predictions split into 6810 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5278
  Batch size = 16


Post-processing 4517 example predictions split into 5278 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: offset_mapping, example_id. If offset_mapping, example_id are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6351
  Batch size = 16


Post-processing 4918 example predictions split into 6351 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'ar.ar': {'exact_match': 34.058106841611995, 'f1': 54.06488681095673}, 'de.de': {'exact_match': 44.941332742971, 'f1': 61.438537161720404}, 'vi.vi': {'exact_match': 44.949954504094634, 'f1': 66.23931584354578}, 'zh.zh': {'exact_match': 35.42923885536305, 'f1': 36.163110622425414}, 'en.en': {'exact_match': 61.47540983606557, 'f1': 77.19782703504617}, 'es.es': {'exact_match': 44.850561583856845, 'f1': 67.95643174936002}, 'hi.hi': {'exact_match': 40.6669377795852, 'f1': 60.24994347679992}}


In [ ]:
df_results_translate_train_es_xlm_r = results_df(results_translate_train_es_xlm_r, "Translate-train es XLM-R")
df_results_translate_train_es_xlm_r.to_csv("results/mlqa/results_translate_train_es_xlm_r.csv")
df_results_translate_train_es_xlm_r

lang  F1_Translate-train es XLM-R  EM_Translate-train es XLM-R
0  ar.ar                        54.06                        34.06
1  de.de                        61.44                        44.94
2  vi.vi                        66.24                        44.95
3  zh.zh                        36.16                        35.43
4  en.en                        77.20                        61.48
5  es.es                        67.96                        44.85
6  hi.hi                        60.25                        40.67
7    avg                        60.47                        43.77

## Translate Train De XLM-R

In [18]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "saattrupdan/xlmr-base-texas-squad-de"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlmr-base-texas-squad-de",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

Downloading:   0%|          | 0.00/716 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.03G [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/398 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/4.83M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/8.66M [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/239 [00:00<?, ?B/s]

In [19]:
split = "test"
map_datasets(langs_translate_train, split, prepare_validation_features)

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/12 [00:00<?, ?ba/s]

  0%|          | 0/6 [00:00<?, ?ba/s]

  0%|          | 0/5 [00:00<?, ?ba/s]

In [22]:
split = "test"
results_translate_train_de_xlm_r = compute_results(langs_translate_train, split)
print(results_translate_train_de_xlm_r)

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6810
  Batch size = 16


Post-processing 5335 example predictions split into 6810 features.


  0%|          | 0/5335 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 5278
  Batch size = 16


Post-processing 4517 example predictions split into 5278 features.


...

  0%|          | 0/5253 [00:00<?, ?it/s]

The following columns in the test set don't have a corresponding argument in `XLMRobertaForQuestionAnswering.forward` and have been ignored: example_id, offset_mapping. If example_id, offset_mapping are not expected by `XLMRobertaForQuestionAnswering.forward`,  you can safely ignore this message.
***** Running Prediction *****
  Num examples = 6351
  Batch size = 16


Post-processing 4918 example predictions split into 6351 features.


  0%|          | 0/4918 [00:00<?, ?it/s]

{'ar.ar': {'exact_match': 35.57638238050609, 'f1': 53.56701458447857}, 'de.de': {'exact_match': 46.690281160061986, 'f1': 62.3615905084792}, 'vi.vi': {'exact_match': 45.18653321201092, 'f1': 64.96355281383701}, 'zh.zh': {'exact_match': 37.37590033093245, 'f1': 38.08811578618861}, 'en.en': {'exact_match': 63.56341673856773, 'f1': 77.26382410562886}, 'es.es': {'exact_match': 45.002855511136495, 'f1': 65.5957160902892}, 'hi.hi': {'exact_match': 43.757625050833674, 'f1': 60.10052798128951}}


In [23]:
df_results_translate_train_de_xlm_r = results_df(results_translate_train_de_xlm_r, "Translate-train de XLM-R")
df_results_translate_train_de_xlm_r.to_csv("results/mlqa/results_translate_train_de_xlm_r.csv")
df_results_translate_train_de_xlm_r

lang  F1_Translate-train de XLM-R  EM_Translate-train de XLM-R
0  ar.ar                        53.57                        35.58
1  de.de                        62.36                        46.69
2  vi.vi                        64.96                        45.19
3  zh.zh                        38.09                        37.38
4  en.en                        77.26                        63.56
5  es.es                        65.60                        45.00
6  hi.hi                        60.10                        43.76
7    avg                        60.28                        45.31

## Translate Train All mBERT

We also experiment with a multi-task version of the translate-train setting where we fine-tune mBERT on the combined translated training data of all languages jointly.

In [ ]:
from transformers import AutoModelForQuestionAnswering, TrainingArguments, Trainer

model_name = "bert-base-multilingual-cased"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)

batch_size = 16

training_args = TrainingArguments(
    output_dir="bert-base-multilingual-cased-squad-all",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
    push_to_hub=True
)

In [ ]:
split = "train"
map_datasets(langs_translate_train_all, split, prepare_train_features)

split = "validation"
map_datasets(langs_translate_train_all, split, prepare_train_features)

In [ ]:
from datasets import DatasetDict, concatenate_datasets

xquad_merged = DatasetDict()
xquad_merged["train"] = squad_train["train"]
xquad_merged["validation"] = squad_train["validation"]

for lang in langs_translate_train_all:
    for split in ["train", "validation"]:
        xquad_merged[split] = concatenate_datasets([xquad_merged[split], xquad_prep[lang][split]])

In [ ]:
xquad_merged

In [ ]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=xquad_merged["train"],
    eval_dataset=xquad_merged["validation"],
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
# trainer.train()

In [ ]:
split = "test"
map_datasets(langs_translate_train, split, prepare_validation_features)

In [ ]:
split = "test"
results_translate_train_all_mbert = compute_results(langs_translate_train, split)
print(results_translate_train_all_mbert)

In [ ]:
df_results_translate_train_all_mbert = results_df(results_translate_train_all_mbert, "TTr_all_mbert")
df_results_translate_train_all_mbert.to_csv("results/mlqa/results_translate_train_all_mbert.csv")
df_results_translate_train_all_mbert

In [ ]:
trainer.push_to_hub()

## Fine-tuning XQuAD mBERT

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "alon-albalak/bert-base-multilingual-xquad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bert-base-multilingual-xquad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
langs = ["ar", "de", "zh", "vi", "en", "es", "hi", "el", "th", "tr", "ru", "ro"]
split = "test"

map_datasets(langs, split, prepare_validation_features)

In [ ]:
results_fine_tuning_xquad_mbert = compute_results(langs, split)
print(results_fine_tuning_xquad_mbert)

In [ ]:
df_results_fine_tuning_xquad_mbert = results_df(results_fine_tuning_xquad_mbert, "FT_xquad_mbert")
df_results_fine_tuning_xquad_mbert.to_csv("results/mlqa/results_fine_tuning_xquad_mbert.csv")
df_results_fine_tuning_xquad_mbert

## Fine-tuning XQuAD XLM-R

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "alon-albalak/xlm-roberta-base-xquad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-base-xquad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
langs = ["ar", "de", "zh", "vi", "en", "es", "hi", "el", "th", "tr", "ru", "ro"]
split = "test"

map_datasets(langs, split, prepare_validation_features)

In [ ]:
results_fine_tuning_xquad_xlm_r = compute_results(langs, split)
print(results_fine_tuning_xquad_xlm_r)

In [ ]:
df_results_fine_tuning_xquad_xlm_r = results_df(results_fine_tuning_xquad_xlm_r, "FT_xquad_xlm_r")
df_results_fine_tuning_xquad_xlm_r.to_csv("results/mlqa/results_fine_tuning_xquad_xlm_r.csv")
df_results_fine_tuning_xquad_xlm_r

## FIne-tuning XQuAD XLM-R-large

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "alon-albalak/xlm-roberta-large-xquad"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="xlm-roberta-large-xquad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
langs = ["ar", "de", "zh", "vi", "en", "es", "hi", "el", "th", "tr", "ru", "ro"]
split = "test"

map_datasets(langs, split, prepare_validation_features)

In [ ]:
results_fine_tuning_xquad_xlm_r_large = compute_results(langs, split)
print(results_fine_tuning_xquad_xlm_r_large)

In [ ]:
df_results_fine_tuning_xquad_xlm_r_large = results_df(results_fine_tuning_xquad_xlm_r_large, "FT_xquad_xml_r_large")
df_results_fine_tuning_xquad_xlm_r_large.to_csv("results/mlqa/results_fine_tuning_xquad_xlm_r_large.csv")
df_results_fine_tuning_xquad_xlm_r_large

## Data Augmentation mBERT

In [ ]:
from transformers import AutoModelForQuestionAnswering, AutoTokenizer, TrainingArguments, Trainer, DefaultDataCollator

model_name = "mrm8488/bert-multi-cased-finetuned-xquadv1"
model = AutoModelForQuestionAnswering.from_pretrained(model_name)
tokenizer = AutoTokenizer.from_pretrained(model_name)
data_collator = DefaultDataCollator()

batch_size = 16
training_args = TrainingArguments(
    output_dir="bert-multi-cased-finetuned-xquadv1",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=None,
    eval_dataset=None,
    tokenizer=tokenizer,
    data_collator=data_collator,
)

In [ ]:
langs = ["ar", "de", "zh", "vi", "en", "es", "hi", "el", "th", "tr", "ru", "ro"]
split = "test"

map_datasets(langs, split, prepare_validation_features)

In [ ]:
results_data_augmentation_mbert = compute_results(langs, split)
print(results_data_augmentation_mbert)

In [ ]:
df_results_data_augmentation_mbert = results_df(results_data_augmentation_mbert, "data_augm_mbert")
df_results_data_augmentation_mbert.to_csv("results/mlqa/results_data_augmentation_mbert.csv")
df_results_data_augmentation_mbert

## Baselines

The MLQA [paper](http://arxiv.org/abs/1910.07475) presents several baselines for zero-shot experiments on MLQA, with training QA data taken from SQuAD V1.1, and using the MLQA English development set for early stopping.

The F1 scores for zero-shot transfer from training with english questions and documents to target language questions and documents are shown below (see the paper for further details). There is lots of room for improvement, and we hope the community will engage in this QA challenge.

| Model F1 Score | en | es | de | ar | hi| vi | zh | 
|:--- |:---: |:---: | :---: |:---: | :---: | :---: | :---: | 
BERT-Large    | **80.2**| - | - | - |- |- |- |
Multilingual-BERT  | 77.7| 64.3| 57.9| 45.7| 43.8| 57.1| 57.5|
XLM    |74.9| **68.0**| **62.2**|**54.8**| 48.8| 61.4| 61.1|
Translate-test BERT-L    | -| 65.4 | 57.9 | 33.6 | 23.8 | 58.2 |44.2 |
Translate-train M-BERT    | - | 53.9 | 62.0  | 51.8 | **55.0**| **62.0**| **61.4** |
Translate-train XLM    | -| 65.2| 61.4| 54.0| 50.7| 59.3| 59.8 |

## Results


In [28]:
import pandas as pd

df_results_zero_shot_mbert = pd.read_csv('results/mlqa/results_zero_shot_mbert.csv')
df_results_zero_shot_xlm_r = pd.read_csv('results/mlqa/results_zero_shot_xlm_r.csv')
df_results_zero_shot_xlm_r_large = pd.read_csv("results/mlqa/results_zero_shot_xlm_r_large.csv")
df_results_translate_test_mbert = pd.read_csv("results/mlqa/results_translate_test_mbert.csv")
df_results_translate_test_bert = pd.read_csv("results/mlqa/results_translate_test_bert.csv")
df_results_translate_test_bert_large = pd.read_csv("results/mlqa/results_translate_test_bert_large.csv")
df_results_translate_test_xlm_r = pd.read_csv("results/mlqa/results_translate_test_xlm_r.csv")
df_results_translate_test_xlm_r_large = pd.read_csv("results/mlqa/results_translate_test_xlm_r_large.csv")
df_results_translate_test_roberta = pd.read_csv("results/mlqa/results_translate_test_roberta.csv")
df_results_translate_test_roberta_large = pd.read_csv("results/mlqa/results_translate_test_roberta_large.csv")
df_results_translate_train_es_xlm_r = pd.read_csv("results/mlqa/results_translate_train_es_xlm_r.csv")
df_results_translate_train_de_xlm_r = pd.read_csv("results/mlqa/results_translate_train_de_xlm_r.csv")
#df_results_fine_tuning_mbert = pd.read_csv("results/mlqa/results_fine_tuning_xquad_mbert.csv")
#df_results_fine_tuning_xquad_xlm_r = pd.read_csv("results/mlqa/results_fine_tuning_xquad_xlm_r.csv")
#df_results_fine_tuning_xquad_xml_r_large = pd.read_csv("results/mlqa/results_fine_tuning_xquad_xlm_r_large.csv")
#df_results_data_augmentation_mbert = pd.read_csv("results/mlqa/results_data_augmentation_mbert.csv")


dataframes = [df_results_zero_shot_mbert, 
              df_results_zero_shot_xlm_r, 
              df_results_zero_shot_xlm_r_large, 
              df_results_translate_test_mbert, 
              df_results_translate_test_bert, 
              df_results_translate_test_bert_large, 
              df_results_translate_test_xlm_r, 
              df_results_translate_test_xlm_r_large, 
              df_results_translate_test_roberta, 
              df_results_translate_test_roberta_large, 
              df_results_translate_train_es_xlm_r, 
              df_results_translate_train_de_xlm_r,
#              df_results_fine_tuning_mbert,
#              df_results_fine_tuning_xquad_xlm_r,
#              df_results_fine_tuning_xquad_xml_r_large,
#              df_results_data_augmentation_mbert, 
              ]

In [29]:
dfs = []
for df in dataframes:
    name1 = list(df.columns)[2]
    name2 = list(df.columns)[3]
    name = name1[3:]
    df = df.round(1)
    df = df.astype({name1: 'str', name2: 'str'}) #float to string
    df[name] = df[[name1, name2]].apply(lambda x: ' / '.join(x), axis=1) #concat F1 and EM
    df = df.drop([name1, name2,"Unnamed: 0"], axis=1) #remove useless columns
    df = df.set_index('lang').T #rotate dataframe
    dfs.append(df)

In [34]:
display(results_df)

lang                                ar.ar        ar.de        ar.vi  \
Zero-shot mBERT               44.9 / 28.0  46.3 / 30.5  35.9 / 20.1   
Zero-shot XML-R               54.6 / 36.0  34.2 / 19.8   15.0 / 5.7   
Zero-shot XML-R Large         62.0 / 42.1  59.7 / 41.8  48.6 / 30.7   
Translate-test mBERT                  NaN          NaN          NaN   
Translate-test BERT                   NaN          NaN          NaN   
Translate-test BERT Large             NaN          NaN          NaN   
Translate-test XLM-R                  NaN          NaN          NaN   
Translate-test XLM-R Large            NaN          NaN          NaN   
Translate-test RoBERTa                NaN          NaN          NaN   
Translate-test RoBERTa Large          NaN          NaN          NaN   
Translate-train es XLM-R      54.1 / 34.1          NaN          NaN   
Translate-train de XLM-R      53.6 / 35.6          NaN          NaN   

lang                                ar.zh        ar.en        ar.es  \
Zero-shot mBERT               36.8 / 21.3  51.1 / 33.7  45.4 / 28.7   
Zero-shot XML-R                14.1 / 5.1  51.5 / 33.8  27.0 / 13.5   
Zero-shot XML-R Large         38.7 / 21.6  61.7 / 42.2  56.7 / 38.4   
Translate-test mBERT                  NaN          NaN          NaN   
Translate-test BERT                   NaN          NaN          NaN   
Translate-test BERT Large             NaN          NaN          NaN   
Translate-test XLM-R                  NaN          NaN          NaN   
Translate-test XLM-R Large            NaN          NaN          NaN   
Translate-test RoBERTa                NaN          NaN          NaN   
Translate-test RoBERTa Large          NaN          NaN          NaN   
Translate-train es XLM-R              NaN          NaN          NaN   
Translate-train de XLM-R              NaN          NaN          NaN   

lang                                ar.hi        de.ar        de.de  \
Zero-shot mBERT               30.8 / 17.3  36.8 / 23.6  59.4 / 43.8   
Zero-shot XML-R                15.6 / 5.8  22.2 / 12.1  62.2 / 46.7   
Zero-shot XML-R Large         43.9 / 27.4  31.2 / 19.5  68.5 / 52.4   
Translate-test mBERT                  NaN          NaN          NaN   
Translate-test BERT                   NaN          NaN          NaN   
Translate-test BERT Large             NaN          NaN          NaN   
Translate-test XLM-R                  NaN          NaN          NaN   
Translate-test XLM-R Large            NaN          NaN          NaN   
Translate-test RoBERTa                NaN          NaN          NaN   
Translate-test RoBERTa Large          NaN          NaN          NaN   
Translate-train es XLM-R              NaN          NaN  61.4 / 44.9   
Translate-train de XLM-R              NaN          NaN  62.4 / 46.7   

lang                                de.vi  ...        hi.en        hi.es  \
Zero-shot mBERT               43.6 / 29.6  ...  52.9 / 37.1  43.7 / 29.1   
Zero-shot XML-R               28.7 / 16.2  ...  60.6 / 43.4  37.4 / 23.0   
Zero-shot XML-R Large         50.7 / 34.3  ...  70.5 / 52.6  63.2 / 45.9   
Translate-test mBERT                  NaN  ...          NaN          NaN   
Translate-test BERT                   NaN  ...          NaN          NaN   
Translate-test BERT Large             NaN  ...          NaN          NaN   
Translate-test XLM-R                  NaN  ...          NaN          NaN   
Translate-test XLM-R Large            NaN  ...          NaN          NaN   
Translate-test RoBERTa                NaN  ...          NaN          NaN   
Translate-test RoBERTa Large          NaN  ...          NaN          NaN   
Translate-train es XLM-R              NaN  ...          NaN          NaN   
Translate-train de XLM-R              NaN  ...          NaN          NaN   

lang                                hi.hi          avg translate-test.ar  \
Zero-shot mBERT               46.2 / 30.0  46.0 / 32.4               NaN   
Zero-shot XML-R               61.4 / 44.2  37.0 / 24.8               NaN   
Zero-shot X

In [35]:
results_df = pd.concat(dfs, axis=0)
# reorder languages to match baseline
results_df = results_df[['en.en', 'es.es', 'de.de', 'ar.ar', 'hi.hi', 'vi.vi', 'zh.zh', translate-test 'avg']]
# rename rows
rows = ["Zero-shot mBERT", "Zero-shot XLM-R", "Zero-shot XLM-R Large", 
        "Translate-test mBERT", "Translate-test BERT", "Translate-test BERT Large",
        "Translate-test XLM-R", "Translate-test XLM-R Large", "Translate-test RoBERTa",
        "Translate-test RoBERTa Large", "Translate-train es XLM-R", "Translate-train de XLM-R"]
results_df = results_df.rename(dict(zip(results_df.index, rows)))
results_df.to_csv("results/mlqa/results.csv")
display(results_df)

lang                                en.en        es.es        de.de  \
Zero-shot mBERT               80.3 / 67.0  64.9 / 43.6  59.4 / 43.8   
Zero-shot XLM-R               80.8 / 68.0  66.5 / 46.1  62.2 / 46.7   
Zero-shot XLM-R Large         84.0 / 71.2  72.1 / 50.2  68.5 / 52.4   
Translate-test mBERT                  NaN          NaN          NaN   
Translate-test BERT                   NaN          NaN          NaN   
Translate-test BERT Large             NaN          NaN          NaN   
Translate-test XLM-R                  NaN          NaN          NaN   
Translate-test XLM-R Large            NaN          NaN          NaN   
Translate-test RoBERTa                NaN          NaN          NaN   
Translate-test RoBERTa Large          NaN          NaN          NaN   
Translate-train es XLM-R      77.2 / 61.5  68.0 / 44.8  61.4 / 44.9   
Translate-train de XLM-R      77.3 / 63.6  65.6 / 45.0  62.4 / 46.7   

lang                                ar.ar        hi.hi        vi.vi  \
Zero-shot mBERT               44.9 / 28.0  46.2 / 30.0  58.8 / 39.6   
Zero-shot XLM-R               54.6 / 36.0  61.4 / 44.2  67.2 / 46.3   
Zero-shot XLM-R Large         62.0 / 42.1  69.8 / 51.3  73.1 / 51.8   
Translate-test mBERT                  NaN          NaN          NaN   
Translate-test BERT                   NaN          NaN          NaN   
Translate-test BERT Large             NaN          NaN          NaN   
Translate-test XLM-R                  NaN          NaN          NaN   
Translate-test XLM-R Large            NaN          NaN          NaN   
Translate-test RoBERTa                NaN          NaN          NaN   
Translate-test RoBERTa Large          NaN          NaN          NaN   
Translate-train es XLM-R      54.1 / 34.1  60.2 / 40.7  66.2 / 45.0   
Translate-train de XLM-R      53.6 / 35.6  60.1 / 43.8  65.0 / 45.2   

lang                                zh.zh          avg  
Zero-shot mBERT               37.4 / 36.8  46.0 / 32.4  
Zero-shot XLM-R               40.0 / 39.3  37.0 / 24.8  
Zero-shot XLM-R Large         45.7 / 45.1  52.7 / 38.3  
Translate-test mBERT                  NaN  53.1 / 32.1  
Translate-test BERT                   NaN  54.1 / 32.9  
Translate-test BERT Large             NaN  56.4 / 34.6  
Translate-test XLM-R                  NaN  53.9 / 32.9  
Translate-test XLM-R Large            NaN  56.7 / 35.0  
Translate-test RoBERTa                NaN  54.3 / 32.3  
Translate-test RoBERTa Large          NaN  56.9 / 35.0  
Translate-train es XLM-R      36.2 / 35.4  60.5 / 43.8  
Translate-train de XLM-R      38.1 / 37.4  60.3 / 45.3

In [ ]:
results_df.to_markdown()